In [1]:
!pip install torch torchvision opencv-python-headless
!pip install openai
!pip install opencv-python pillow requests
!pip install matplotlib
!pip install matplotlib opencv-python-headless
!pip install pillow
!pip install cucim[plugins]

In [2]:
# Install the CUDA 12 specific version of cuCIM
!pip install cucim-cu12

# Install CuPy for CUDA 12
!pip install cupy-cuda12x

# Install the required image format plugins
!pip install pylibcucim-cu12

In [3]:
from IPython.display import display, Image, Audio
import openai
import cv2  # We're using OpenCV to read video, to install !pip install opencv-python
import base64
import time
from openai import OpenAI
import os
import requests
import torch

In [4]:
# In a Python cell
!lspci | grep -i nvidia
!nvidia-smi
!nvcc --version
!which python
!python --version

0000:17:00.0 VGA compatible controller: NVIDIA Corporation GA102GL [RTX A6000] (rev a1)
0000:17:00.1 Audio device: NVIDIA Corporation GA102 High Definition Audio Controller (rev a1)
0000:65:00.0 VGA compatible controller: NVIDIA Corporation GA102GL [RTX A6000] (rev a1)
0000:65:00.1 Audio device: NVIDIA Corporation GA102 High Definition Audio Controller (rev a1)
Tue Jun 24 13:41:44 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 570.133.07             Driver Version: 570.133.07     CUDA Version: 12.8     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+=========

In [5]:
!nvidia-smi

Tue Jun 24 13:41:46 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 570.133.07             Driver Version: 570.133.07     CUDA Version: 12.8     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA RTX A6000               Off |   00000000:17:00.0 Off |                  Off |
| 30%   28C    P5             20W /  300W |      15MiB /  49140MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------------------------+-----

In [6]:
import torch

print(torch.cuda.is_available())  # Should return True
print(torch.cuda.current_device())  # Should return 0
print(torch.cuda.get_device_name(0))  # Should return "NVIDIA RTX A6000" (not A100)
!nvidia-smi

True
0
NVIDIA RTX A6000
Tue Jun 24 13:41:46 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 570.133.07             Driver Version: 570.133.07     CUDA Version: 12.8     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA RTX A6000               Off |   00000000:17:00.0 Off |                  Off |
| 30%   28C    P5             24W /  300W |      18MiB /  49140MiB |      0%      Default |
|                                         |                        |                  N/A |
+-----------------------

In [7]:
f = open("/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt", "r")
mykey = f.read()

#ZER0-SHOT
* Clear, direct instructions
* No examples or demonstrations
* No training or fine-tuning
* Each task stands alone

Implementation:
* Like being given a task with no examples or practice
* Direct analysis without prior context
* Each question stands alone
* No dependencies between questions
* Like taking a test without studying examples first

In [8]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from concurrent.futures import ThreadPoolExecutor
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/ZERO"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class ZeroShotGeminiAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use correct model name - try stable 2.0 Flash first
        self.model_name = "gemini-2.0-flash"  # Stable model
        # Alternative preview models (uncomment if you specifically need 2.5 features):
        # self.model_name = "gemini-2.5-flash-preview-05-20"  # Preview model
        # self.model_name = "gemini-1.5-pro"  # Fallback option (may have restrictions)

        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.max_frames_per_request = 20
        self.chunk_size = 10
        os.makedirs(self.save_dir, exist_ok=True)

    def process_frames_in_chunks(self, prompt, frame_data):
        """Process frames in chunks using Gemini API"""
        all_responses = []

        # Process frames in chunks
        for i in range(0, len(frame_data), self.chunk_size):
            chunk = frame_data[i:i + self.chunk_size]

            # Prepare content array for Gemini
            parts = [
                {
                    "text": prompt
                }
            ]

            # Add each frame to the parts
            for frame in chunk:
                parts.append({
                    "inline_data": {
                        "mime_type": "image/png",
                        "data": frame
                    }
                })

            # Make API request to Gemini
            payload = {
                "contents": [
                    {
                        "parts": parts
                    }
                ],
                "generationConfig": {
                    "temperature": 0.1,
                    "maxOutputTokens": 4096,
                    "topP": 0.8,
                    "topK": 10
                }
            }

            try:
                print(f"Sending chunk {i//self.chunk_size + 1}/{(len(frame_data) + self.chunk_size - 1)//self.chunk_size} to Gemini...")

                # Add API key as query parameter
                url_with_key = f"{self.base_url}?key={self.api_key}"
                response = requests.post(url_with_key, headers=self.headers, json=payload)

                # IMPROVED: Better error handling
                if response.status_code != 200:
                    try:
                        error_detail = response.json()
                    except:
                        error_detail = response.text

                    print(f"API Error {response.status_code}: {error_detail}")

                    # Check for specific errors and provide solutions
                    if response.status_code == 404:
                        print(f"Model '{self.model_name}' not found. Try updating the model name.")
                        print("Available stable models: gemini-2.0-flash")
                        print("Preview models: gemini-2.5-flash-preview-05-20")

                    all_responses.append(f"Error {response.status_code}: {error_detail}")
                    continue

                result = response.json()
                if "candidates" in result and result["candidates"]:
                    if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                        response_content = result["candidates"][0]["content"]["parts"][0]["text"]
                        print(f"Received response for chunk {i//self.chunk_size + 1}")
                        all_responses.append(response_content)
                    else:
                        all_responses.append(f"Error: No content in response for chunk {i//self.chunk_size + 1}")
                else:
                    all_responses.append(f"Error: No candidates in response for chunk {i//self.chunk_size + 1}")

            except Exception as e:
                print(f"Error for chunk {i//self.chunk_size + 1}: {str(e)}")
                all_responses.append(f"Error: {str(e)}")

            # Rate limiting - Gemini has different rate limits
            print(f"Waiting 2 seconds before next request...")
            time.sleep(2)

        # Combine all chunk responses
        combined_response = "\n\n=== NEXT CHUNK ===\n\n".join(all_responses)
        return combined_response

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with pure zero-shot approach"""
        try:
            frame_names = list(frames_data.keys())

            # Improved sorting function for frame numbers
            def extract_frame_number(filename):
                try:
                    # Handle different naming patterns
                    if '_frame_' in filename:
                        parts = filename.split('_frame_')
                        if len(parts) > 1:
                            number_part = parts[1].split('.')[0]
                            return int(number_part)
                    elif 'frame' in filename.lower():
                        # Alternative pattern matching
                        import re
                        numbers = re.findall(r'\d+', filename)
                        if numbers:
                            return int(numbers[-1])  # Use the last number found
                except Exception as e:
                    print(f"Error extracting frame number from {filename}: {str(e)}")
                    return 0

            sorted_frames = sorted(frame_names, key=extract_frame_number)

            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Frame names sample: {sorted_frames[:5]}{'...' if len(sorted_frames) > 5 else ''}")

            results = {}
            timestamp = time.strftime("%Y%m%d_%H%M%S")

            # ==========================================
            # PURE ZERO-SHOT PROMPT TECHNIQUE
            # ==========================================
            # NO examples, NO formatting instructions, NO few-shot demonstrations
            # NO chain-of-thought prompting, NO specific output structure requirements
            # Just a simple, direct question to let the model respond naturally
            prompt = "What's happening in these frames? Describe the scene and any notable actions or events."
            # ==========================================

            try:
                frame_data = [frames_data[frame_name] for frame_name in sorted_frames
                             if frame_name in frames_data and frames_data[frame_name]]

                if not frame_data:
                    answer = "No valid frames were available for analysis."
                    print("WARNING: No valid frames were available for analysis.")
                else:
                    print(f"Processing {len(frame_data)} valid frames...")
                    answer = self.process_frames_in_chunks(prompt, frame_data)

                results["Analysis"] = {
                    "crime_type": crime_type,
                    "model_used": self.model_name,  # Track which model was used
                    "prompting_technique": "PURE_ZERO_SHOT",  # Confirm zero-shot approach
                    "prompt": prompt,
                    "answer": answer,
                    "frames_used": len(sorted_frames),
                    "valid_frames": len(frame_data),
                    "timestamp": timestamp
                }

                # Save results
                self.save_results(results, f"{crime_type}_{video_id}_zero_shot_analysis_{timestamp}.json")
                print(f"Analysis for {video_id} ({crime_type}) completed and saved.")

            except Exception as e:
                print(f"Error processing analysis: {str(e)}")
                results["Analysis"] = {
                    "crime_type": crime_type,
                    "model_used": self.model_name,
                    "prompting_technique": "PURE_ZERO_SHOT",  # Confirm zero-shot approach
                    "prompt": prompt,
                    "error": str(e),
                    "frames_used": len(sorted_frames),
                    "timestamp": timestamp
                }

            return results

        except Exception as e:
            print(f"Error in analyze_frames: {str(e)}")
            raise

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with zero-shot analysis - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = ZeroShotGeminiAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH PURE ZERO-SHOT ANALYSIS 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 Zero-Shot Mode: No prompting tricks, just natural AI responses!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with zero-shot approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key}")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"zero_shot_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection with multiple model options"""
    print("Testing Gemini API connection...")

    # Test models in order of preference
    test_models = [
        "gemini-2.0-flash",  # Stable model, best option
        "gemini-2.5-flash-preview-05-20",  # Preview model
        "gemini-1.5-pro",  # Fallback (may have restrictions)
    ]

    for model_name in test_models:
        print(f"\nTesting model: {model_name}")
        url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

        headers = {
            "Content-Type": "application/json"
        }

        payload = {
            "contents": [
                {
                    "parts": [
                        {
                            "text": "Hello, can you respond with 'API connection successful'?"
                        }
                    ]
                }
            ]
        }

        try:
            response = requests.post(url, headers=headers, json=payload)

            if response.status_code == 200:
                result = response.json()
                if "candidates" in result and result["candidates"]:
                    if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                        response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                        print(f"✓ {model_name} connection successful!")
                        print(f"Response: {response_text}")
                        return True, model_name
                print(f"✗ Unexpected response format for {model_name}")
                print(f"Response: {result}")
            else:
                print(f"✗ API Error {response.status_code} for {model_name}: {response.text}")

        except Exception as e:
            print(f"✗ Connection error for {model_name}: {str(e)}")

    print("✗ All model tests failed.")
    return False, None

def check_authentication():
    """Placeholder function to check authentication"""
    return True

def run():
    """Main execution function"""
    print("PURE Zero-Shot Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*70)
    print("🔥 ZERO-SHOT TECHNIQUE: No examples, no formatting, no demonstrations!")
    print("   Just pure, natural AI response to simple descriptive questions")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*70)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection with multiple models
    api_test_success, working_model = test_gemini_api(api_key)
    if not api_test_success:
        print("✗ All Gemini API tests failed. Please check your API key and connection.")
        print("\nTroubleshooting tips:")
        print("1. Verify your API key is correct")
        print("2. Check if your account has access to Gemini models")
        print("3. Try using gemini-1.5-pro if 2.0+ models aren't available")
        return

    print(f"✓ Will use model: {working_model}")

    # Check authentication
    if not check_authentication():
        print("✗ Authentication not completed.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)

    for video_id, video_results in results.items():
        if video_results and 'Analysis' in video_results:
            total_frames_processed += video_results['Analysis'].get('valid_frames', 0)

    print("\n" + "="*70)
    print(f"🎉 COMPLETE FOLDER PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Model used: {working_model}")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("="*70)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
PURE Zero-Shot Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🔥 ZERO-SHOT TECHNIQUE: No examples, no formatting, no demonstrations!
   Just pure, natural AI response to simple descriptive questions
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/ZERO
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...

Testing model: gemini-2.0-flash
✓ gemini-2.0-flash connection successful!
Response: API connection successful

✓ Will use model: gemini-2.0-flash

Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTI

#Sequential Prompting:
In sequential prompting, we build upon previous answers, using them to inform subsequent prompts in a sequence. This creates a chain of prompts where each builds on what came before.

1. Sequential Prompting Implementation
Key Features:

Processes all frames in chunks of 10 frames each
Uses a progressive sequence of 5 prompts that build on each previous response:

- High-level scene description
- People identification and actions
- Potential criminal activities
- Objects/items involved in the incident
- Chronological timeline of events


Includes a final synthesis step that consolidates findings across all chunks

Implementation Highlights:

- Each step processes all chunks independently
- Previous step responses are provided as context for each new step
- Results from all chunks are combined before proceeding to the next step
- Saves intermediate results after each step for monitoring progress



In [9]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/SEQUENTIAL"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class SequentialPromptingAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use the same working model as the zero-shot script
        self.model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.chunk_size = 10
        os.makedirs(self.save_dir, exist_ok=True)

        # Sequential prompting flow - each prompt builds on previous responses
        self.prompt_sequence = [
            "What's happening in these frames? Describe the scene at a high level.",
            "Based on what you observed in your previous response, who are the main people in the scene and what are they doing?",
            "Looking at the actions you described, do you observe any potential criminal activities? If so, describe them in detail.",
            "Based on your crime analysis, what objects or items are involved in the incident?",
            "Considering all your observations, create a chronological timeline of events shown in these frames."
        ]

    def convert_conversation_to_gemini_format(self, conversation, new_user_content):
        """Convert conversation history to Gemini format"""
        contents = []

        # Skip system message as Gemini doesn't use system messages the same way
        for i in range(1, len(conversation)):  # Start from 1 to skip system message
            message = conversation[i]
            if message["role"] == "user":
                # For user messages, we need to handle both text and image content
                if isinstance(message["content"], list):
                    # This is a complex message with images - convert to parts
                    parts = []
                    for content_item in message["content"]:
                        if content_item["type"] == "text":
                            parts.append({"text": content_item["text"]})
                        elif content_item["type"] == "image_url":
                            # Extract base64 data from data URL
                            data_url = content_item["image_url"]["url"]
                            if data_url.startswith("data:"):
                                mime_type, base64_data = data_url.split(",", 1)
                                mime_type = mime_type.split(":")[1].split(";")[0]
                                parts.append({
                                    "inline_data": {
                                        "mime_type": mime_type,
                                        "data": base64_data
                                    }
                                })
                    contents.append({"role": "user", "parts": parts})
                else:
                    # Simple text message
                    contents.append({"role": "user", "parts": [{"text": message["content"]}]})
            elif message["role"] == "assistant":
                contents.append({"role": "model", "parts": [{"text": message["content"]}]})

        # Add the new user content
        if isinstance(new_user_content, list):
            parts = []
            for content_item in new_user_content:
                if content_item["type"] == "text":
                    parts.append({"text": content_item["text"]})
                elif content_item["type"] == "image_url":
                    data_url = content_item["image_url"]["url"]
                    if data_url.startswith("data:"):
                        mime_type, base64_data = data_url.split(",", 1)
                        mime_type = mime_type.split(":")[1].split(";")[0]
                        parts.append({
                            "inline_data": {
                                "mime_type": mime_type,
                                "data": base64_data
                            }
                        })
            contents.append({"role": "user", "parts": parts})
        else:
            contents.append({"role": "user", "parts": [{"text": new_user_content}]})

        return contents

    def process_frames_with_sequential_prompts(self, frames_data, video_id, crime_type):
        """Process frames with sequential prompting approach"""
        # Extract frame data from the dictionary
        frame_names = list(frames_data.keys())

        # Improved sorting function for frame numbers
        def extract_frame_number(filename):
            try:
                # Handle different naming patterns
                if '_frame_' in filename:
                    parts = filename.split('_frame_')
                    if len(parts) > 1:
                        number_part = parts[1].split('.')[0]
                        return int(number_part)
                elif 'frame' in filename.lower():
                    # Alternative pattern matching
                    import re
                    numbers = re.findall(r'\d+', filename)
                    if numbers:
                        return int(numbers[-1])  # Use the last number found
            except Exception as e:
                print(f"Error extracting frame number from {filename}: {str(e)}")
                return 0

        sorted_frames = sorted(frame_names, key=extract_frame_number)
        frame_data = [frames_data[frame_name] for frame_name in sorted_frames if frame_name in frames_data and frames_data[frame_name]]

        if not frame_data:
            return {"error": "No valid frames available for analysis"}

        total_frames = len(frame_data)
        print(f"Processing all {total_frames} frames for sequential analysis")

        # Process all frames by dividing them into chunks
        chunk_size = 10
        frame_chunks = [frame_data[i:i+chunk_size] for i in range(0, total_frames, chunk_size)]
        print(f"Split into {len(frame_chunks)} chunks of approximately {chunk_size} frames each")

        # Initialize conversation history
        conversation = [
            {
                "role": "system",
                "content": "You are analyzing video frames showing a potential crime scene. Provide detailed observations based on what you see."
            }
        ]

        sequence_results = {}
        all_chunk_responses = {}

        # Process each prompt in sequence
        for step, prompt in enumerate(self.prompt_sequence, 1):
            print(f"Processing sequential prompt {step}/{len(self.prompt_sequence)}")

            # For each step, collect responses from all chunks
            step_responses = []

            # Process each chunk of frames for this step
            for chunk_idx, chunk in enumerate(frame_chunks):
                print(f"  Processing chunk {chunk_idx+1}/{len(frame_chunks)} for step {step}...")

                # Create a clean conversation state for each chunk that includes previous steps
                # but starts fresh for this chunk
                if step == 1:
                    # First step only needs system message
                    chunk_conversation = [conversation[0]]
                else:
                    # Later steps include previous step responses in conversation
                    chunk_conversation = [conversation[0]]
                    for prev_step in range(1, step):
                        # Include previous prompt
                        chunk_conversation.append({
                            "role": "user",
                            "content": self.prompt_sequence[prev_step-1]
                        })
                        # Include aggregated response from previous step
                        chunk_conversation.append({
                            "role": "assistant",
                            "content": all_chunk_responses[f"Step {prev_step}"]
                        })

                # Create the user message with prompt and frames
                user_message_content = [
                    {
                        "type": "text",
                        "text": f"{prompt} (Analyzing frames {chunk_idx*chunk_size+1}-{min((chunk_idx+1)*chunk_size, total_frames)} of {total_frames})"
                    }
                ]

                # Include frames for this chunk
                for frame in chunk:
                    # Default to PNG since the files are PNGs
                    mime_type = "image/png"

                    user_message_content.append({
                        "type": "image_url",
                        "image_url": {
                            "url": f"data:{mime_type};base64,{frame}",
                            "detail": "high"
                        }
                    })

                # Convert conversation to Gemini format
                gemini_contents = self.convert_conversation_to_gemini_format(chunk_conversation, user_message_content)

                # Make API request for this chunk
                payload = {
                    "contents": gemini_contents,
                    "generationConfig": {
                        "temperature": 0.1,
                        "maxOutputTokens": 4096,
                        "topP": 0.8,
                        "topK": 10
                    }
                }

                try:
                    print(f"    Sending request to Gemini for chunk {chunk_idx+1}...")
                    url_with_key = f"{self.base_url}?key={self.api_key}"
                    response = requests.post(url_with_key, headers=self.headers, json=payload)

                    if response.status_code != 200:
                        error_detail = response.json() if response.text else response.text
                        print(f"    API Error {response.status_code}: {error_detail}")
                        step_responses.append(f"Error processing chunk {chunk_idx+1}: {error_detail}")
                        continue

                    result = response.json()
                    if "candidates" in result and result["candidates"]:
                        if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                            assistant_response = result["candidates"][0]["content"]["parts"][0]["text"]
                            print(f"    Received response for chunk {chunk_idx+1}")
                            step_responses.append(assistant_response)
                        else:
                            step_responses.append(f"No content in response for chunk {chunk_idx+1}")
                    else:
                        step_responses.append(f"No candidates in response for chunk {chunk_idx+1}")

                except Exception as e:
                    print(f"    Error in chunk {chunk_idx+1} for step {step}: {str(e)}")
                    step_responses.append(f"Error processing chunk {chunk_idx+1}: {str(e)}")

                # Rate limiting between chunks
                print(f"    Waiting 3 seconds before next request...")
                time.sleep(3)

            # Combine all chunk responses for this step
            combined_response = "\n\n=== NEXT CHUNK ===\n\n".join(step_responses)

            # Save the combined response for this step
            sequence_results[f"Step {step}"] = {
                "prompt": prompt,
                "response": combined_response
            }

            # Store for use in next steps
            all_chunk_responses[f"Step {step}"] = combined_response

            # Add to main conversation for later reference
            conversation.append({
                "role": "user",
                "content": prompt
            })
            conversation.append({
                "role": "assistant",
                "content": combined_response
            })

            # Save intermediate results after each step
            timestamp = time.strftime("%Y%m%d_%H%M%S")
            step_result = {
                f"Step {step}": sequence_results[f"Step {step}"]
            }
            self.save_results(step_result, f"{crime_type}_{video_id}_sequential_step{step}_{timestamp}.json")
            print(f"  Step {step} results saved.")

            # Rate limiting between steps
            print(f"  Waiting 5 seconds before next step...")
            time.sleep(5)

        # Add a final synthesis step to bring everything together
        synthesis_prompt = "Based on all your previous analyses of ALL frame chunks, provide a comprehensive final assessment of the entire video. Summarize what crime appears to be taking place, who is involved, and how events unfolded across all the frames."

        # Convert final conversation to Gemini format
        gemini_contents = self.convert_conversation_to_gemini_format(conversation, synthesis_prompt)

        # Make API request for final synthesis
        payload = {
            "contents": gemini_contents,
            "generationConfig": {
                "temperature": 0.1,
                "maxOutputTokens": 4096,
                "topP": 0.8,
                "topK": 10
            }
        }

        try:
            print("Performing final synthesis of all analyses...")
            url_with_key = f"{self.base_url}?key={self.api_key}"
            response = requests.post(url_with_key, headers=self.headers, json=payload)

            if response.status_code == 200:
                result = response.json()
                if "candidates" in result and result["candidates"]:
                    if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                        assistant_response = result["candidates"][0]["content"]["parts"][0]["text"]
                        print("Synthesis complete!")

                        # Save synthesis results
                        sequence_results["Final Synthesis"] = {
                            "prompt": synthesis_prompt,
                            "response": assistant_response
                        }

                        timestamp = time.strftime("%Y%m%d_%H%M%S")
                        synthesis_result = {
                            "Final Synthesis": sequence_results["Final Synthesis"]
                        }
                        self.save_results(synthesis_result, f"{crime_type}_{video_id}_sequential_synthesis_{timestamp}.json")
                        print("Synthesis results saved.")
                else:
                    print("No content in synthesis response")
            else:
                error_detail = response.json() if response.text else response.text
                print(f"API Error in synthesis: {response.status_code}: {error_detail}")

        except Exception as e:
            print(f"Error in final synthesis: {str(e)}")

        return {
            "sequential_results": sequence_results,
            "frames_used": total_frames,
            "chunks_processed": len(frame_chunks),
            "frames_per_chunk": chunk_size,
            "model_used": self.model_name,  # Track which model was used
            "crime_type": crime_type,
            "prompting_technique": "SEQUENTIAL_PROMPTING",
            "timestamp": time.strftime("%Y%m%d_%H%M%S")
        }

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with sequential prompting"""
        try:
            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) WITH SEQUENTIAL PROMPTING ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Using model: {self.model_name}")

            timestamp = time.strftime("%Y%m%d_%H%M%S")
            results = self.process_frames_with_sequential_prompts(frames_data, video_id, crime_type)

            # Save complete results
            self.save_results(results, f"{crime_type}_{video_id}_sequential_complete_{timestamp}.json")
            print(f"Complete sequential analysis for {video_id} ({crime_type}) saved.")

            return results

        except Exception as e:
            print(f"Error in sequential analysis: {str(e)}")
            return {"error": str(e)}

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with sequential prompting - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = SequentialPromptingAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH SEQUENTIAL PROMPTING 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 Sequential Mode: Building analysis step by step!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with sequential prompting approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key} with sequential prompting")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"sequential_prompting_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete sequential analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection"""
    print("Testing Gemini API connection...")

    # FIXED: Use the same working model
    model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
    url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

    headers = {
        "Content-Type": "application/json"
    }

    payload = {
        "contents": [
            {
                "parts": [
                    {
                        "text": "Hello, can you respond with 'API connection successful'?"
                    }
                ]
            }
        ]
    }

    try:
        response = requests.post(url, headers=headers, json=payload)

        if response.status_code == 200:
            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                    print("✓ Gemini API connection successful!")
                    print(f"Response: {response_text}")
                    return True
            print("✗ Unexpected response format")
            print(f"Response: {result}")
            return False
        else:
            print(f"✗ API Error {response.status_code}: {response.text}")
            return False

    except Exception as e:
        print(f"✗ Connection error: {str(e)}")
        return False

def run():
    """Main execution function"""
    print("Sequential Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*70)
    print("🎯 SEQUENTIAL TECHNIQUE: Building analysis step by step through guided prompts!")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*70)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection
    if not test_gemini_api(api_key):
        print("✗ Gemini API test failed. Please check your API key and connection.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING WITH SEQUENTIAL PROMPTING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)

    for video_id, video_results in results.items():
        if video_results and 'frames_used' in video_results:
            total_frames_processed += video_results.get('frames_used', 0)

    print("\n" + "="*70)
    print(f"🎉 COMPLETE SEQUENTIAL PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Model used: {analyzer.model_name if 'analyzer' in locals() else 'gemini-2.0-flash'}")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("🎯 Sequential prompting technique applied to all videos")
    print("="*70)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
Sequential Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🎯 SEQUENTIAL TECHNIQUE: Building analysis step by step through guided prompts!
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/SEQUENTIAL
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...
✓ Gemini API connection successful!
Response: API connection successful


Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTING COMPLETE FOLDER PROCESSING WITH SEQUENTIAL PROMPTING...

=== DISCOVERING ALL VIDEOS AND FRAMES ===
Scanning director

#Least-To-Most Prompting
2. Least-To-Most Prompting Implementation
Key Features:

Processes all frames in chunks of 10 frames each
Uses a sequence of 8 prompts with increasing complexity:

- Simple object identification (low complexity)
- People identification (low complexity)
- Location/setting description (low complexity)
- Basic action identification (low complexity)
- Interaction analysis (medium complexity)
- Unusual behavior detection (medium complexity)
- Criminal activity analysis (high complexity)
- Comprehensive timeline (high complexity)


Includes a final comprehensive assessment that integrates all analyses

Implementation Highlights:

- Each step clearly labeled with its complexity level (Low, Medium, High)
- Builds from simple identification tasks to complex analysis
- Each chunk gets analyzed separately, with results combined before the next step
- Previous observation steps provide context for later analytical steps

In [10]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/LEAST-TO-MOST"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class LeastToMostAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use the same working model as the other scripts
        self.model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.chunk_size = 10
        os.makedirs(self.save_dir, exist_ok=True)

        # Least-to-Most prompting sequence - starts with simpler tasks and gradually increases complexity
        self.prompt_sequence = [
            # Simple object and scene identification
            "List all visible objects in these frames. Just identify what you can see - furniture, tools, vehicles, etc.",

            # Simple people identification
            "Identify the people visible in these frames. How many are there? Describe each person's basic appearance (clothing, general features).",

            # Simple spatial relationships
            "Describe the location and setting shown in these frames. What kind of place is this? Describe the spatial layout.",

            # Basic actions (still simple)
            "What actions are the people performing in these frames? List simple actions you can observe.",

            # Interactions (medium complexity)
            "How are the people interacting with each other and with objects in the scene? Describe specific interactions.",

            # Unusual behaviors (medium complexity)
            "Do you notice any unusual, concerning, or potentially suspicious behaviors in these frames? If so, what specifically seems unusual?",

            # Criminal analysis (higher complexity)
            "Based on your previous observations, analyze whether any potential criminal activities might be occurring. What specific elements suggest criminal behavior?",

            # Comprehensive timeline (highest complexity)
            "Using all your previous observations, construct a detailed chronological timeline of events shown in these frames. Include who did what, when, and potential motives."
        ]

    def convert_conversation_to_gemini_format(self, conversation, new_user_content):
        """Convert conversation history to Gemini format"""
        contents = []

        # Skip system message as Gemini doesn't use system messages the same way
        for i in range(1, len(conversation)):  # Start from 1 to skip system message
            message = conversation[i]
            if message["role"] == "user":
                # For user messages, we need to handle both text and image content
                if isinstance(message["content"], list):
                    # This is a complex message with images - convert to parts
                    parts = []
                    for content_item in message["content"]:
                        if content_item["type"] == "text":
                            parts.append({"text": content_item["text"]})
                        elif content_item["type"] == "image_url":
                            # Extract base64 data from data URL
                            data_url = content_item["image_url"]["url"]
                            if data_url.startswith("data:"):
                                mime_type, base64_data = data_url.split(",", 1)
                                mime_type = mime_type.split(":")[1].split(";")[0]
                                parts.append({
                                    "inline_data": {
                                        "mime_type": mime_type,
                                        "data": base64_data
                                    }
                                })
                    contents.append({"role": "user", "parts": parts})
                else:
                    # Simple text message
                    contents.append({"role": "user", "parts": [{"text": message["content"]}]})
            elif message["role"] == "assistant":
                contents.append({"role": "model", "parts": [{"text": message["content"]}]})

        # Add the new user content
        if isinstance(new_user_content, list):
            parts = []
            for content_item in new_user_content:
                if content_item["type"] == "text":
                    parts.append({"text": content_item["text"]})
                elif content_item["type"] == "image_url":
                    data_url = content_item["image_url"]["url"]
                    if data_url.startswith("data:"):
                        mime_type, base64_data = data_url.split(",", 1)
                        mime_type = mime_type.split(":")[1].split(";")[0]
                        parts.append({
                            "inline_data": {
                                "mime_type": mime_type,
                                "data": base64_data
                            }
                        })
            contents.append({"role": "user", "parts": parts})
        else:
            contents.append({"role": "user", "parts": [{"text": new_user_content}]})

        return contents

    def process_frames_with_least_to_most(self, frames_data, video_id, crime_type):
        """Process frames with least-to-most prompting approach"""
        # Extract frame data from the dictionary
        frame_names = list(frames_data.keys())

        # Improved sorting function for frame numbers
        def extract_frame_number(filename):
            try:
                # Handle different naming patterns
                if '_frame_' in filename:
                    parts = filename.split('_frame_')
                    if len(parts) > 1:
                        number_part = parts[1].split('.')[0]
                        return int(number_part)
                elif 'frame' in filename.lower():
                    # Alternative pattern matching
                    import re
                    numbers = re.findall(r'\d+', filename)
                    if numbers:
                        return int(numbers[-1])  # Use the last number found
            except Exception as e:
                print(f"Error extracting frame number from {filename}: {str(e)}")
                return 0

        sorted_frames = sorted(frame_names, key=extract_frame_number)
        frame_data = [frames_data[frame_name] for frame_name in sorted_frames if frame_name in frames_data and frames_data[frame_name]]

        if not frame_data:
            return {"error": "No valid frames available for analysis"}

        total_frames = len(frame_data)
        print(f"Processing all {total_frames} frames for least-to-most analysis")

        # Process all frames by dividing them into chunks
        chunk_size = 10
        frame_chunks = [frame_data[i:i+chunk_size] for i in range(0, total_frames, chunk_size)]
        print(f"Split into {len(frame_chunks)} chunks of approximately {chunk_size} frames each")

        # Initialize conversation history with system message
        conversation = [
            {
                "role": "system",
                "content": "You are analyzing video frames from a potential crime scene. Start with basic observations and gradually build to more complex analysis as directed by the prompts."
            }
        ]

        ltm_results = {}
        all_chunk_responses = {}

        # Process each prompt in sequence, building complexity
        for step, prompt in enumerate(self.prompt_sequence, 1):
            print(f"Processing least-to-most prompt {step}/{len(self.prompt_sequence)}: {prompt[:30]}...")

            # For each step, collect responses from all chunks
            step_responses = []

            # Process each chunk of frames for this step
            for chunk_idx, chunk in enumerate(frame_chunks):
                print(f"  Processing chunk {chunk_idx+1}/{len(frame_chunks)} for step {step}...")

                # Create a clean conversation state for each chunk that includes previous steps
                # but starts fresh for this chunk
                if step == 1:
                    # First step only needs system message
                    chunk_conversation = [conversation[0]]
                else:
                    # Later steps include previous step responses in conversation
                    chunk_conversation = [conversation[0]]
                    for prev_step in range(1, step):
                        # Include previous prompt
                        chunk_conversation.append({
                            "role": "user",
                            "content": self.prompt_sequence[prev_step-1]
                        })
                        # Include aggregated response from previous step
                        chunk_conversation.append({
                            "role": "assistant",
                            "content": all_chunk_responses[f"Step {prev_step}"]
                        })

                # Create the user message with prompt and frames
                user_message_content = [
                    {
                        "type": "text",
                        "text": f"{prompt} (Analyzing frames {chunk_idx*chunk_size+1}-{min((chunk_idx+1)*chunk_size, total_frames)} of {total_frames})"
                    }
                ]

                # Include frames for this chunk
                for frame in chunk:
                    # Default to PNG since the files are PNGs
                    mime_type = "image/png"

                    user_message_content.append({
                        "type": "image_url",
                        "image_url": {
                            "url": f"data:{mime_type};base64,{frame}",
                            "detail": "high"
                        }
                    })

                # Convert conversation to Gemini format
                gemini_contents = self.convert_conversation_to_gemini_format(chunk_conversation, user_message_content)

                # Make API request for this chunk
                payload = {
                    "contents": gemini_contents,
                    "generationConfig": {
                        "temperature": 0.1,
                        "maxOutputTokens": 4096,
                        "topP": 0.8,
                        "topK": 10
                    }
                }

                try:
                    print(f"    Sending request to Gemini for chunk {chunk_idx+1}...")
                    url_with_key = f"{self.base_url}?key={self.api_key}"
                    response = requests.post(url_with_key, headers=self.headers, json=payload)

                    if response.status_code != 200:
                        error_detail = response.json() if response.text else response.text
                        print(f"    API Error {response.status_code}: {error_detail}")
                        step_responses.append(f"Error processing chunk {chunk_idx+1}: {error_detail}")
                        continue

                    result = response.json()
                    if "candidates" in result and result["candidates"]:
                        if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                            assistant_response = result["candidates"][0]["content"]["parts"][0]["text"]
                            print(f"    Received response for chunk {chunk_idx+1}")
                            step_responses.append(assistant_response)
                        else:
                            step_responses.append(f"No content in response for chunk {chunk_idx+1}")
                    else:
                        step_responses.append(f"No candidates in response for chunk {chunk_idx+1}")

                except Exception as e:
                    print(f"    Error in chunk {chunk_idx+1} for step {step}: {str(e)}")
                    step_responses.append(f"Error processing chunk {chunk_idx+1}: {str(e)}")

                # Rate limiting between chunks
                print(f"    Waiting 3 seconds before next request...")
                time.sleep(3)

            # Combine all chunk responses for this step
            combined_response = "\n\n=== NEXT CHUNK ===\n\n".join(step_responses)

            # Save the combined response for this step
            ltm_results[f"Step {step}"] = {
                "prompt": prompt,
                "complexity_level": "Low" if step <= 3 else "Medium" if step <= 6 else "High",
                "response": combined_response
            }

            # Store for use in next steps
            all_chunk_responses[f"Step {step}"] = combined_response

            # Add to main conversation for the final synthesis
            conversation.append({
                "role": "user",
                "content": prompt
            })
            conversation.append({
                "role": "assistant",
                "content": combined_response
            })

            # Save intermediate results after each step
            timestamp = time.strftime("%Y%m%d_%H%M%S")
            step_result = {
                f"Step {step}": ltm_results[f"Step {step}"]
            }
            self.save_results(step_result, f"{crime_type}_{video_id}_ltm_step{step}_{timestamp}.json")
            print(f"  Step {step} results saved.")

            # Rate limiting between steps
            print(f"  Waiting 5 seconds before next step...")
            time.sleep(5)

        # Add a final synthesis prompt to integrate all previous analyses
        if len(ltm_results) == len(self.prompt_sequence):
            print("Performing final synthesis of all analyses...")
            synthesis_prompt = "Based on all your previous analyses of ALL frame chunks, provide a comprehensive assessment of what crime appears to be taking place, who is involved, how it was executed, and what evidence is visible in the frames."

            # Convert final conversation to Gemini format
            gemini_contents = self.convert_conversation_to_gemini_format(conversation, synthesis_prompt)

            # Make API request for final synthesis
            payload = {
                "contents": gemini_contents,
                "generationConfig": {
                    "temperature": 0.1,
                    "maxOutputTokens": 4096,
                    "topP": 0.8,
                    "topK": 10
                }
            }

            try:
                url_with_key = f"{self.base_url}?key={self.api_key}"
                response = requests.post(url_with_key, headers=self.headers, json=payload)

                if response.status_code == 200:
                    result = response.json()
                    if "candidates" in result and result["candidates"]:
                        if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                            assistant_response = result["candidates"][0]["content"]["parts"][0]["text"]
                            print("Synthesis complete!")

                            # Save synthesis results
                            ltm_results["Final Synthesis"] = {
                                "prompt": synthesis_prompt,
                                "complexity_level": "Highest",
                                "response": assistant_response
                            }

                            timestamp = time.strftime("%Y%m%d_%H%M%S")
                            synthesis_result = {
                                "Final Synthesis": ltm_results["Final Synthesis"]
                            }
                            self.save_results(synthesis_result, f"{crime_type}_{video_id}_ltm_synthesis_{timestamp}.json")
                            print("Synthesis results saved.")
                    else:
                        print("No content in synthesis response")
                else:
                    error_detail = response.json() if response.text else response.text
                    print(f"API Error in synthesis: {response.status_code}: {error_detail}")
            except Exception as e:
                print(f"Error in final synthesis: {str(e)}")

        return {
            "least_to_most_results": ltm_results,
            "frames_used": total_frames,
            "chunks_processed": len(frame_chunks),
            "frames_per_chunk": chunk_size,
            "model_used": self.model_name,  # Track which model was used
            "crime_type": crime_type,
            "prompting_technique": "LEAST_TO_MOST_PROMPTING",
            "timestamp": time.strftime("%Y%m%d_%H%M%S")
        }

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with least-to-most prompting"""
        try:
            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) WITH LEAST-TO-MOST PROMPTING ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Using model: {self.model_name}")

            timestamp = time.strftime("%Y%m%d_%H%M%S")
            results = self.process_frames_with_least_to_most(frames_data, video_id, crime_type)

            # Save complete results
            self.save_results(results, f"{crime_type}_{video_id}_ltm_complete_{timestamp}.json")
            print(f"Complete least-to-most analysis for {video_id} ({crime_type}) saved.")

            return results

        except Exception as e:
            print(f"Error in least-to-most analysis: {str(e)}")
            return {"error": str(e)}

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with least-to-most prompting - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = LeastToMostAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH LEAST-TO-MOST PROMPTING 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 Least-to-Most Mode: Building from simple to complex analysis!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with least-to-most prompting approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key} with least-to-most prompting")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"least_to_most_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete least-to-most analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection"""
    print("Testing Gemini API connection...")

    # FIXED: Use the same working model
    model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
    url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

    headers = {
        "Content-Type": "application/json"
    }

    payload = {
        "contents": [
            {
                "parts": [
                    {
                        "text": "Hello, can you respond with 'API connection successful'?"
                    }
                ]
            }
        ]
    }

    try:
        response = requests.post(url, headers=headers, json=payload)

        if response.status_code == 200:
            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                    print("✓ Gemini API connection successful!")
                    print(f"Response: {response_text}")
                    return True
            print("✗ Unexpected response format")
            print(f"Response: {result}")
            return False
        else:
            print(f"✗ API Error {response.status_code}: {response.text}")
            return False

    except Exception as e:
        print(f"✗ Connection error: {str(e)}")
        return False

def run():
    """Main execution function"""
    print("Least-To-Most Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*70)
    print("🎯 LEAST-TO-MOST TECHNIQUE: Building from simple to complex analysis step by step!")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*70)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection
    if not test_gemini_api(api_key):
        print("✗ Gemini API test failed. Please check your API key and connection.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING WITH LEAST-TO-MOST PROMPTING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)

    for video_id, video_results in results.items():
        if video_results and 'frames_used' in video_results:
            total_frames_processed += video_results.get('frames_used', 0)

    print("\n" + "="*70)
    print(f"🎉 COMPLETE LEAST-TO-MOST PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Model used: {analyzer.model_name if 'analyzer' in locals() else 'gemini-2.0-flash'}")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("🎯 Least-to-Most prompting technique applied to all videos")
    print("="*70)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
Least-To-Most Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🎯 LEAST-TO-MOST TECHNIQUE: Building from simple to complex analysis step by step!
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/LEAST-TO-MOST
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...
✓ Gemini API connection successful!
Response: API connection successful


Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTING COMPLETE FOLDER PROCESSING WITH LEAST-TO-MOST PROMPTING...

=== DISCOVERING ALL VIDEOS AND FRAMES ===
Scann

#ReAct
ReAct Prompting Approach
The ReAct technique follows a structured thinking cycle:

- Thought: Reasoning about what's being observed and its potential meaning
- Action: Deciding what specific aspect to focus on analyzing next
- Observation: Making detailed observations about that specific aspect
- Decision: Drawing a conclusion based on accumulated observations

Implementation Highlights

Explicit ReAct Framework:

- The prompt explicitly guides the model through the four-step cycle (Thought → Action → Observation → Decision)
- Applies this cycle to multiple aspects: people, actions, objects, spatial relationships, etc.


Complete Frame Processing:

- Processes all frames in chunks of 10 frames each
- Each chunk gets a full ReAct analysis independently


Evidence Chain Analysis:

- After all chunks are processed, a second pass synthesizes all analysis chunks
- Creates a coherent evidence chain that resolves any contradictions between chunks
- Explicitly establishes what crime occurred, who was involved, and the sequence of events
- Assesses confidence level in the final determination


Distinct Prompting Strategy:

- Unlike sequential or least-to-most approaches, ReAct emphasizes explicit reasoning Forces the model to justify conclusions with evidence
Creates a clear chain of reasoning that mimics human investigative processes



Benefits of ReAct for Crime Analysis
The ReAct approach is particularly well-suited for crime analysis because:

- Transparency: The reasoning and decision process is explicit and traceable
- Evidence-Based: Conclusions are directly linked to specific observations
- Methodical: Forces a structured investigation approach rather than jumping to conclusions
- Forensic-Style: Resembles how human investigators approach crime scenes

The final step, which combines all chunk analyses into a cohesive evidence chain, ensures that the entire video is considered holistically despite being processed in chunks. This produces a comprehensive analysis that identifies consistent evidence across the entire video sequence.
This implementation provides a robust framework for analyzing crime videos that explicitly shows the reasoning process behind each conclusion, making it particularly valuable for scenarios where explaining the rationale is as important as the conclusions themselves.

In [11]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/REACT"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class ReActAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use the same working model as the other scripts
        self.model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.chunk_size = 10
        os.makedirs(self.save_dir, exist_ok=True)

        # Base ReAct prompt that guides the model through a reasoning and acting cycle
        self.react_prompt_template = """
Analyze these frames using the ReAct approach (Reasoning and Acting). For each important element you observe:

1. Thought: Reason about what you're seeing and what it might mean
2. Action: Describe what specific aspect you'll focus on analyzing next
3. Observation: Make detailed observations about that aspect
4. Decision: Draw a conclusion based on your observations

Specifically, follow this cycle for:
- People and their appearances
- Actions and behaviors
- Objects and items
- Spatial relationships
- Temporal sequence of events
- Potential criminal activity

After going through these cycles, provide your final analysis of what crime appears to be occurring, who is involved, and what evidence supports this conclusion.

You are now analyzing frames {frame_range} of {total_frames}.
"""

    def convert_conversation_to_gemini_format(self, conversation, new_user_content):
        """Convert conversation history to Gemini format"""
        contents = []

        # Skip system message as Gemini doesn't use system messages the same way
        for i in range(1, len(conversation)):  # Start from 1 to skip system message
            message = conversation[i]
            if message["role"] == "user":
                # For user messages, we need to handle both text and image content
                if isinstance(message["content"], list):
                    # This is a complex message with images - convert to parts
                    parts = []
                    for content_item in message["content"]:
                        if content_item["type"] == "text":
                            parts.append({"text": content_item["text"]})
                        elif content_item["type"] == "image_url":
                            # Extract base64 data from data URL
                            data_url = content_item["image_url"]["url"]
                            if data_url.startswith("data:"):
                                mime_type, base64_data = data_url.split(",", 1)
                                mime_type = mime_type.split(":")[1].split(";")[0]
                                parts.append({
                                    "inline_data": {
                                        "mime_type": mime_type,
                                        "data": base64_data
                                    }
                                })
                    contents.append({"role": "user", "parts": parts})
                else:
                    # Simple text message
                    contents.append({"role": "user", "parts": [{"text": message["content"]}]})
            elif message["role"] == "assistant":
                contents.append({"role": "model", "parts": [{"text": message["content"]}]})

        # Add the new user content
        if isinstance(new_user_content, list):
            parts = []
            for content_item in new_user_content:
                if content_item["type"] == "text":
                    parts.append({"text": content_item["text"]})
                elif content_item["type"] == "image_url":
                    data_url = content_item["image_url"]["url"]
                    if data_url.startswith("data:"):
                        mime_type, base64_data = data_url.split(",", 1)
                        mime_type = mime_type.split(":")[1].split(";")[0]
                        parts.append({
                            "inline_data": {
                                "mime_type": mime_type,
                                "data": base64_data
                            }
                        })
            contents.append({"role": "user", "parts": parts})
        else:
            contents.append({"role": "user", "parts": [{"text": new_user_content}]})

        return contents

    def process_frames_with_react(self, frames_data, video_id, crime_type):
        """Process frames with ReAct prompting approach"""
        # Extract frame data from the dictionary
        frame_names = list(frames_data.keys())

        # Improved sorting function for frame numbers
        def extract_frame_number(filename):
            try:
                # Handle different naming patterns
                if '_frame_' in filename:
                    parts = filename.split('_frame_')
                    if len(parts) > 1:
                        number_part = parts[1].split('.')[0]
                        return int(number_part)
                elif 'frame' in filename.lower():
                    # Alternative pattern matching
                    import re
                    numbers = re.findall(r'\d+', filename)
                    if numbers:
                        return int(numbers[-1])  # Use the last number found
            except Exception as e:
                print(f"Error extracting frame number from {filename}: {str(e)}")
                return 0

        sorted_frames = sorted(frame_names, key=extract_frame_number)
        frame_data = [frames_data[frame_name] for frame_name in sorted_frames if frame_name in frames_data and frames_data[frame_name]]

        if not frame_data:
            return {"error": "No valid frames available for analysis"}

        total_frames = len(frame_data)
        print(f"Processing all {total_frames} frames with ReAct approach")

        # Process all frames by dividing them into chunks
        chunk_size = 10
        frame_chunks = [frame_data[i:i+chunk_size] for i in range(0, total_frames, chunk_size)]
        print(f"Split into {len(frame_chunks)} chunks of approximately {chunk_size} frames each")

        # Initialize results and conversation
        react_results = {}
        all_chunk_analysis = []

        # System message that sets up the ReAct approach
        system_message = {
            "role": "system",
            "content": "You are an expert crime scene analyst using the ReAct approach to analyze video frames. First reason about what you see (Thought), then decide what to focus on (Action), then make detailed observations (Observation), and finally draw conclusions (Decision). Be methodical and evidence-based."
        }

        # Process each chunk of frames
        for chunk_idx, chunk in enumerate(frame_chunks):
            frame_start = chunk_idx * chunk_size + 1
            frame_end = min((chunk_idx + 1) * chunk_size, total_frames)
            frame_range = f"{frame_start}-{frame_end}"

            print(f"Processing chunk {chunk_idx+1}/{len(frame_chunks)} (frames {frame_range})...")

            # Create the prompt for this chunk
            react_prompt = self.react_prompt_template.format(frame_range=frame_range, total_frames=total_frames)

            # Reset conversation for each chunk
            chunk_conversation = [system_message]

            # Create user message with prompt and frames
            user_message_content = [
                {
                    "type": "text",
                    "text": react_prompt
                }
            ]

            # Add frames to the message
            for frame in chunk:
                # Default to PNG since the files are PNGs
                mime_type = "image/png"

                user_message_content.append({
                    "type": "image_url",
                    "image_url": {
                        "url": f"data:{mime_type};base64,{frame}",
                        "detail": "high"
                    }
                })

            # Convert conversation to Gemini format
            gemini_contents = self.convert_conversation_to_gemini_format(chunk_conversation, user_message_content)

            # Make API request for initial ReAct analysis
            payload = {
                "contents": gemini_contents,
                "generationConfig": {
                    "temperature": 0.1,
                    "maxOutputTokens": 4096,
                    "topP": 0.8,
                    "topK": 10
                }
            }

            try:
                print(f"  Sending request to Gemini for chunk {chunk_idx+1}...")
                url_with_key = f"{self.base_url}?key={self.api_key}"
                response = requests.post(url_with_key, headers=self.headers, json=payload)

                if response.status_code != 200:
                    error_detail = response.json() if response.text else response.text
                    print(f"  API Error {response.status_code}: {error_detail}")
                    chunk_analysis = f"Error processing chunk {chunk_idx+1}: {error_detail}"
                else:
                    result = response.json()
                    if "candidates" in result and result["candidates"]:
                        if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                            chunk_analysis = result["candidates"][0]["content"]["parts"][0]["text"]
                            print(f"  Received response for chunk {chunk_idx+1}")
                        else:
                            chunk_analysis = f"No content in response for chunk {chunk_idx+1}"
                    else:
                        chunk_analysis = f"No candidates in response for chunk {chunk_idx+1}"

                # Save analysis for this chunk
                react_results[f"Chunk {chunk_idx+1}"] = {
                    "frame_range": frame_range,
                    "react_analysis": chunk_analysis
                }

                # Append to collection of all analyses
                all_chunk_analysis.append(chunk_analysis)

                # Save intermediate results for this chunk
                timestamp = time.strftime("%Y%m%d_%H%M%S")
                chunk_result = {
                    f"Chunk {chunk_idx+1}": react_results[f"Chunk {chunk_idx+1}"]
                }
                self.save_results(chunk_result, f"{crime_type}_{video_id}_react_chunk{chunk_idx+1}_{timestamp}.json")
                print(f"  Chunk {chunk_idx+1} results saved.")

            except Exception as e:
                print(f"  Error in chunk {chunk_idx+1}: {str(e)}")
                react_results[f"Chunk {chunk_idx+1}"] = {
                    "frame_range": frame_range,
                    "error": str(e)
                }

            # Rate limiting between chunks
            print(f"  Waiting 3 seconds before next request...")
            time.sleep(3)

        # After processing all chunks, perform a comprehensive evidence chain analysis
        if all_chunk_analysis:
            print("Performing comprehensive evidence chain analysis across all chunks...")

            # Create a combined conversation for the evidence chain analysis
            # Create chunk analysis text separately to avoid f-string backslash issues
            chunk_analyses_text = ""
            separator = "-" * 40

            for i, analysis in enumerate(all_chunk_analysis):
                start_frame = i * chunk_size + 1
                end_frame = min((i + 1) * chunk_size, total_frames)
                chunk_text = f"CHUNK {i+1} (Frames {start_frame}-{end_frame}):\n{analysis}\n\n{separator}\n"
                chunk_analyses_text += chunk_text

            evidence_chain_prompt = f"""
I have analyzed a crime scene video in {len(frame_chunks)} chunks using the ReAct approach. Below are the analyses for each chunk of frames.

Your task:
1. Review all chunk analyses
2. Identify consistent evidence across chunks
3. Resolve any contradictions between chunks
4. Construct a single coherent narrative of the crime
5. List the evidence that supports your conclusions
6. Assess confidence in your final determination

Here are the chunk analyses:

{separator}
{chunk_analyses_text}

Based on all this evidence, provide your final analysis of what crime occurred, who was involved, and how it happened.
"""

            # Convert to Gemini format for evidence chain analysis
            evidence_chain_contents = [
                {
                    "role": "user",
                    "parts": [
                        {
                            "text": evidence_chain_prompt
                        }
                    ]
                }
            ]

            # Make API request for evidence chain analysis
            payload = {
                "contents": evidence_chain_contents,
                "generationConfig": {
                    "temperature": 0.1,
                    "maxOutputTokens": 4096,
                    "topP": 0.8,
                    "topK": 10
                }
            }

            try:
                print("Sending request for evidence chain analysis...")
                url_with_key = f"{self.base_url}?key={self.api_key}"
                response = requests.post(url_with_key, headers=self.headers, json=payload)

                if response.status_code == 200:
                    result = response.json()
                    if "candidates" in result and result["candidates"]:
                        if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                            evidence_chain_analysis = result["candidates"][0]["content"]["parts"][0]["text"]
                            print("Evidence chain analysis complete!")

                            # Save evidence chain analysis
                            react_results["Evidence Chain Analysis"] = {
                                "analysis": evidence_chain_analysis
                            }

                            # Save evidence chain separately
                            timestamp = time.strftime("%Y%m%d_%H%M%S")
                            evidence_chain_result = {
                                "Evidence Chain Analysis": react_results["Evidence Chain Analysis"]
                            }
                            self.save_results(evidence_chain_result, f"{crime_type}_{video_id}_react_evidence_chain_{timestamp}.json")
                            print("Evidence chain analysis saved.")
                        else:
                            print("No content in evidence chain response")
                    else:
                        print("No candidates in evidence chain response")
                else:
                    error_detail = response.json() if response.text else response.text
                    print(f"API Error in evidence chain analysis: {response.status_code}: {error_detail}")
            except Exception as e:
                print(f"Error in evidence chain analysis: {str(e)}")
                react_results["Evidence Chain Analysis"] = {
                    "error": str(e)
                }

        return {
            "react_results": react_results,
            "frames_used": total_frames,
            "chunks_processed": len(frame_chunks),
            "frames_per_chunk": chunk_size,
            "model_used": self.model_name,  # Track which model was used
            "crime_type": crime_type,
            "prompting_technique": "REACT_PROMPTING",
            "timestamp": time.strftime("%Y%m%d_%H%M%S")
        }

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with ReAct prompting"""
        try:
            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) WITH REACT PROMPTING ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Using model: {self.model_name}")

            timestamp = time.strftime("%Y%m%d_%H%M%S")
            results = self.process_frames_with_react(frames_data, video_id, crime_type)

            # Save complete results
            self.save_results(results, f"{crime_type}_{video_id}_react_complete_{timestamp}.json")
            print(f"Complete ReAct analysis for {video_id} ({crime_type}) saved.")

            return results

        except Exception as e:
            print(f"Error in ReAct analysis: {str(e)}")
            return {"error": str(e)}

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with ReAct prompting - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = ReActAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH REACT PROMPTING 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 ReAct Mode: Reasoning and Acting through systematic analysis!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with ReAct prompting approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key} with ReAct prompting")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"react_prompting_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete ReAct analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection"""
    print("Testing Gemini API connection...")

    # FIXED: Use the same working model
    model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
    url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

    headers = {
        "Content-Type": "application/json"
    }

    payload = {
        "contents": [
            {
                "parts": [
                    {
                        "text": "Hello, can you respond with 'API connection successful'?"
                    }
                ]
            }
        ]
    }

    try:
        response = requests.post(url, headers=headers, json=payload)

        if response.status_code == 200:
            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                    print("✓ Gemini API connection successful!")
                    print(f"Response: {response_text}")
                    return True
            print("✗ Unexpected response format")
            print(f"Response: {result}")
            return False
        else:
            print(f"✗ API Error {response.status_code}: {response.text}")
            return False

    except Exception as e:
        print(f"✗ Connection error: {str(e)}")
        return False

def run():
    """Main execution function"""
    print("ReAct Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*70)
    print("🎯 REACT TECHNIQUE: Reasoning and Acting through systematic analysis!")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*70)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection
    if not test_gemini_api(api_key):
        print("✗ Gemini API test failed. Please check your API key and connection.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING WITH REACT PROMPTING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)

    for video_id, video_results in results.items():
        if video_results and 'frames_used' in video_results:
            total_frames_processed += video_results.get('frames_used', 0)

    print("\n" + "="*70)
    print(f"🎉 COMPLETE REACT PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Model used: {analyzer.model_name if 'analyzer' in locals() else 'gemini-2.0-flash'}")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("🎯 ReAct prompting technique applied to all videos")
    print("="*70)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
ReAct Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🎯 REACT TECHNIQUE: Reasoning and Acting through systematic analysis!
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/REACT
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...
✓ Gemini API connection successful!
Response: API connection successful


Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTING COMPLETE FOLDER PROCESSING WITH REACT PROMPTING...

=== DISCOVERING ALL VIDEOS AND FRAMES ===
Scanning directory: /home/opade7/Documents

#Iterative prompting
Iterative Prompting Approach
The Iterative Prompting technique follows a structured refinement process:

- Initial Analysis: The model provides a first-pass analysis of what appears to be happening in the frames
- Guided Iterations: Through a series of targeted follow-up prompts, the model refines specific aspects of its analysis
- Progressive Improvement: Each round builds on previous insights while addressing potential weaknesses or gaps
- Final Synthesis: After multiple refinement rounds, the model creates a final, comprehensive assessment

Implementation Highlights

Multi-Round Refinement:

Starts with an initial general analysis prompt
Follows with 4 specialized refinement rounds:

- People and relationships focus
- Actions and intent focus
- Criminal elements and evidence focus
- Critical examination (missing elements, alternative interpretations)


Concludes with a final synthesis prompt for each chunk


Complete Frame Processing:

- Processes all frames in chunks of 10 frames each
- Each chunk undergoes the full iterative process independently


Conversation Continuity:

- Maintains the complete conversation history throughout all rounds
- Each refinement builds on the accumulated context from previous rounds
- Creates a progressive improvement cycle where later responses incorporate earlier insights


Holistic Synthesis:

- After all chunks are iteratively analyzed, performs a final cross-chunk synthesis
- Creates a coherent narrative of the entire incident
- Addresses any discrepancies between chunk analyses

In [12]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from concurrent.futures import ThreadPoolExecutor
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/ITERATIVE"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class TrueIterativeGeminiAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use the same working model as the other scripts
        self.model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.max_frames_per_request = 20
        self.chunk_size = 10
        self.max_iterations = 8  # Maximum iterations before stopping
        self.convergence_threshold = 0.7  # Similarity threshold for convergence
        os.makedirs(self.save_dir, exist_ok=True)

        # Core iterative question that gets refined each time
        self.core_question = "Analyze these video frames for criminal activity. What crime is occurring, who is involved, what evidence supports your conclusion, and how confident are you in this assessment?"

    def make_gemini_request(self, contents):
        """Make a single request to Gemini API"""
        url_with_key = f"{self.base_url}?key={self.api_key}"

        payload = {
            "contents": contents,
            "generationConfig": {
                "temperature": 0.1,
                "maxOutputTokens": 4096,
                "topP": 0.8,
                "topK": 10
            }
        }

        try:
            response = requests.post(url_with_key, headers=self.headers, json=payload)

            if response.status_code != 200:
                error_detail = response.json() if response.text else response.text
                print(f"API Error {response.status_code}: {error_detail}")
                return f"Error {response.status_code}: {error_detail}"

            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    return result["candidates"][0]["content"]["parts"][0]["text"]
                else:
                    return "Error: No content in response"
            else:
                return "Error: No candidates in response"

        except Exception as e:
            print(f"API request error: {str(e)}")
            return f"Error: {str(e)}"

    def calculate_similarity(self, text1, text2):
        """Simple similarity calculation based on word overlap"""
        if not text1 or not text2:
            return 0.0

        # Convert to lowercase and split into words
        words1 = set(text1.lower().split())
        words2 = set(text2.lower().split())

        # Calculate Jaccard similarity
        intersection = words1.intersection(words2)
        union = words1.union(words2)

        if len(union) == 0:
            return 0.0

        return len(intersection) / len(union)

    def has_converged(self, current_response, previous_response):
        """Check if the analysis has converged (responses are very similar)"""
        if not previous_response:
            return False

        similarity = self.calculate_similarity(current_response, previous_response)
        print(f"    Similarity to previous: {similarity:.3f} (threshold: {self.convergence_threshold})")

        return similarity >= self.convergence_threshold

    def extract_confidence_score(self, response):
        """Extract confidence score from response if mentioned"""
        confidence_keywords = ["confidence", "confident", "certainty", "sure", "probability"]
        response_lower = response.lower()

        # Look for percentage mentions
        import re
        percentages = re.findall(r'(\d+)%', response)
        if percentages:
            return max([int(p) for p in percentages]) / 100.0

        # Look for confidence keywords with qualifiers
        if any(keyword in response_lower for keyword in ["very confident", "highly confident", "extremely confident"]):
            return 0.9
        elif any(keyword in response_lower for keyword in ["confident", "fairly confident"]):
            return 0.7
        elif any(keyword in response_lower for keyword in ["somewhat confident", "moderately confident"]):
            return 0.5
        elif any(keyword in response_lower for keyword in ["low confidence", "uncertain", "unsure"]):
            return 0.3

        return 0.5  # Default moderate confidence

    def process_frames_truly_iteratively(self, frame_data, video_id, crime_type):
        """Process frames using TRUE iterative prompting - same question refined repeatedly"""
        all_iterations = {}
        previous_response = None
        converged = False

        print(f"Starting TRUE iterative analysis with max {self.max_iterations} iterations...")
        print(f"Core question: {self.core_question}")
        print(f"Convergence threshold: {self.convergence_threshold}")

        # TRUE ITERATIVE LOOP - Same question, progressively refined
        for iteration_num in range(1, self.max_iterations + 1):
            print(f"\n=== TRUE ITERATION {iteration_num}/{self.max_iterations} ===")

            iteration_responses = []

            # Process frames in chunks for this iteration
            for i in range(0, len(frame_data), self.chunk_size):
                chunk = frame_data[i:i + self.chunk_size]

                # Build TRUE iterative prompt
                if iteration_num == 1:
                    # First iteration - ask the core question
                    iterative_prompt = f"""ITERATION {iteration_num} - Initial Analysis

{self.core_question}

Be thorough and specific in your analysis. Include your confidence level in your assessment."""

                else:
                    # Subsequent iterations - refine based on previous response
                    iterative_prompt = f"""ITERATION {iteration_num} - Refining Previous Analysis

PREVIOUS ANALYSIS FROM ITERATION {iteration_num-1}:
{previous_response[:800]}...

Now, analyze these SAME frames again with the SAME core question, but refine your analysis:

{self.core_question}

REFINEMENT INSTRUCTIONS:
- Review your previous analysis carefully
- Look for details you may have missed
- Reconsider your conclusions with fresh perspective
- Identify any errors or oversights in your previous assessment
- Improve the accuracy and depth of your analysis
- If you're more confident now, explain why
- If you're less confident, explain what creates uncertainty
- What new insights do you have upon re-examination?

Provide your REFINED analysis of the same core question."""

                # Prepare content parts for Gemini
                parts = [{"text": iterative_prompt}]

                # Add images to parts
                for frame in chunk:
                    parts.append({
                        "inline_data": {
                            "mime_type": "image/png",
                            "data": frame
                        }
                    })

                contents = [{
                    "role": "user",
                    "parts": parts
                }]

                print(f"  Processing chunk {i//self.chunk_size + 1}/{(len(frame_data) + self.chunk_size - 1)//self.chunk_size}...")

                # Make API request for this chunk
                response = self.make_gemini_request(contents)
                iteration_responses.append(response)

                # Rate limiting
                print(f"  Waiting 3 seconds before next request...")
                time.sleep(3)

            # Combine responses for this iteration
            if len(iteration_responses) == 1:
                current_response = iteration_responses[0]
            else:
                current_response = "\n\n=== NEXT CHUNK ===\n\n".join(iteration_responses)

            # Extract confidence for this iteration
            confidence = self.extract_confidence_score(current_response)

            # Check for convergence
            if previous_response:
                converged = self.has_converged(current_response, previous_response)

            # Store this iteration's data
            iteration_data = {
                "iteration": iteration_num,
                "type": "true_iterative_refinement",
                "core_question": self.core_question,
                "prompt_used": iterative_prompt,
                "response": current_response,
                "confidence_extracted": confidence,
                "converged": converged,
                "similarity_to_previous": self.calculate_similarity(current_response, previous_response) if previous_response else 0.0
            }

            all_iterations[f"iteration_{iteration_num}"] = iteration_data

            # Save intermediate results after each iteration
            timestamp = time.strftime("%Y%m%d_%H%M%S")
            iteration_result = {
                f"iteration_{iteration_num}": iteration_data
            }
            self.save_results(iteration_result, f"{crime_type}_{video_id}_iterative_iteration{iteration_num}_{timestamp}.json")

            print(f"  Confidence level: {confidence:.2f}")
            print(f"  Response preview: {current_response[:200]}...")

            # Check for convergence
            if converged:
                print(f"  *** CONVERGENCE ACHIEVED at iteration {iteration_num} ***")
                break
            elif iteration_num < self.max_iterations:
                print(f"  Continuing to iteration {iteration_num + 1} (not yet converged)")

            # Update previous response for next iteration
            previous_response = current_response

        # Create convergence summary
        convergence_summary = {
            "total_iterations_run": iteration_num,
            "max_iterations_allowed": self.max_iterations,
            "converged": converged,
            "convergence_threshold": self.convergence_threshold,
            "final_confidence": confidence,
            "methodology": "True iterative refinement - same question refined repeatedly"
        }

        if converged:
            convergence_summary["convergence_iteration"] = iteration_num
            convergence_summary["convergence_reason"] = f"Response similarity reached {self.convergence_threshold} threshold"
        else:
            convergence_summary["convergence_reason"] = f"Maximum iterations ({self.max_iterations}) reached without convergence"

        return all_iterations, convergence_summary

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with TRUE iterative prompting approach"""
        try:
            frame_names = list(frames_data.keys())

            # Improved sorting function for frame numbers
            def extract_frame_number(filename):
                try:
                    # Handle different naming patterns
                    if '_frame_' in filename:
                        parts = filename.split('_frame_')
                        if len(parts) > 1:
                            number_part = parts[1].split('.')[0]
                            return int(number_part)
                    elif 'frame' in filename.lower():
                        # Alternative pattern matching
                        import re
                        numbers = re.findall(r'\d+', filename)
                        if numbers:
                            return int(numbers[-1])  # Use the last number found
                except Exception as e:
                    print(f"Error extracting frame number from {filename}: {str(e)}")
                    return 0

            sorted_frames = sorted(frame_names, key=extract_frame_number)

            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Frame names sample: {sorted_frames[:5]}{'...' if len(sorted_frames) > 5 else ''}")
            print(f"Using model: {self.model_name}")

            results = {}
            timestamp = time.strftime("%Y%m%d_%H%M%S")

            try:
                frame_data = [frames_data[frame_name] for frame_name in sorted_frames
                             if frame_name in frames_data and frames_data[frame_name]]

                if not frame_data:
                    results["True_Iterative_Analysis"] = {
                        "error": "No valid frames were available for analysis.",
                        "frames_used": len(sorted_frames),
                        "valid_frames": 0,
                        "model_used": self.model_name,
                        "crime_type": crime_type,
                        "prompting_technique": "TRUE_ITERATIVE_PROMPTING"
                    }
                    print("WARNING: No valid frames were available for analysis.")
                else:
                    print(f"Processing {len(frame_data)} valid frames with TRUE iterative prompting...")
                    iterative_responses, convergence_summary = self.process_frames_truly_iteratively(frame_data, video_id, crime_type)

                    results["True_Iterative_Analysis"] = {
                        "method": "true_iterative_prompting",
                        "description": "Same question refined repeatedly until convergence",
                        "core_question": self.core_question,
                        "convergence_summary": convergence_summary,
                        "all_iterations": iterative_responses,
                        "frames_used": len(sorted_frames),
                        "valid_frames": len(frame_data),
                        "analysis_timestamp": timestamp,
                        "model_used": self.model_name,
                        "crime_type": crime_type,
                        "prompting_technique": "TRUE_ITERATIVE_PROMPTING"
                    }

                # Save results
                self.save_results(results, f"{crime_type}_{video_id}_true_iterative_analysis_{timestamp}.json")
                print(f"True iterative analysis for {video_id} ({crime_type}) completed and saved.")

            except Exception as e:
                print(f"Error processing true iterative analysis: {str(e)}")
                results["True_Iterative_Analysis"] = {
                    "method": "true_iterative_prompting",
                    "error": str(e),
                    "frames_used": len(sorted_frames) if 'sorted_frames' in locals() else 0,
                    "model_used": self.model_name,
                    "crime_type": crime_type,
                    "prompting_technique": "TRUE_ITERATIVE_PROMPTING"
                }

            return results

        except Exception as e:
            print(f"Error in analyze_frames: {str(e)}")
            raise

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with true iterative analysis - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = TrueIterativeGeminiAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH TRUE ITERATIVE PROMPTING 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 True Iterative Mode: Same question refined repeatedly until convergence!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with true iterative prompting approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key} with true iterative prompting")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"true_iterative_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete TRUE iterative analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection"""
    print("Testing Gemini API connection...")

    # FIXED: Use the same working model
    model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
    url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

    headers = {
        "Content-Type": "application/json"
    }

    payload = {
        "contents": [
            {
                "parts": [
                    {
                        "text": "Hello, can you respond with 'Gemini API connection successful'?"
                    }
                ]
            }
        ]
    }

    try:
        response = requests.post(url, headers=headers, json=payload)

        if response.status_code == 200:
            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                    print("✓ Gemini API connection successful!")
                    print(f"Response: {response_text}")
                    return True
            print("✗ Unexpected response format")
            print(f"Response: {result}")
            return False
        else:
            print(f"✗ API Error {response.status_code}: {response.text}")
            return False

    except Exception as e:
        print(f"✗ Connection error: {str(e)}")
        return False

def check_authentication():
    """Placeholder function to check authentication"""
    return True

def run():
    """Main execution function"""
    print("TRUE Iterative Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*70)
    print("🎯 TRUE ITERATIVE TECHNIQUE: Same question refined repeatedly until convergence!")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*70)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection
    if not test_gemini_api(api_key):
        print("✗ Gemini API test failed. Please check your API key and connection.")
        return

    # Check authentication
    if not check_authentication():
        print("✗ Authentication not completed.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING WITH TRUE ITERATIVE PROMPTING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)
    total_iterations_run = 0
    convergence_achieved = 0

    for video_id, video_results in results.items():
        if video_results and 'True_Iterative_Analysis' in video_results:
            analysis = video_results['True_Iterative_Analysis']
            total_frames_processed += analysis.get('valid_frames', 0)
            if 'convergence_summary' in analysis:
                total_iterations_run += analysis['convergence_summary'].get('total_iterations_run', 0)
                if analysis['convergence_summary'].get('converged', False):
                    convergence_achieved += 1

    print("\n" + "="*70)
    print(f"🎉 COMPLETE TRUE ITERATIVE PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Total iterations run: {total_iterations_run}")
    print(f"Convergence achieved: {convergence_achieved}/{total_videos_processed} videos")
    print(f"Model used: {analyzer.model_name if 'analyzer' in locals() else 'gemini-2.0-flash'}")
    print(f"Method: Same core question refined repeatedly until convergence")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("🎯 True iterative prompting technique applied to all videos")
    print("="*70)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
TRUE Iterative Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🎯 TRUE ITERATIVE TECHNIQUE: Same question refined repeatedly until convergence!
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/ITERATIVE
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...
✓ Gemini API connection successful!
Response: Gemini API connection successful


Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTING COMPLETE FOLDER PROCESSING WITH TRUE ITERATIVE PROMPTING...

=== DISCOVERING ALL VIDEOS AND FRAMES ===
Sc

#Self-Consistency
This approach generates multiple independent analyses and determines the most reliable interpretation through consensus.
Self-Consistency Prompting Approach
The Self-Consistency technique follows a unique multi-analysis process:

Multiple Independent Analyses: The system generates several different analyses of the same frames
Diverse Perspectives: Each analysis uses a different prompt template to encourage varied viewpoints
Consensus Determination: The system identifies areas of agreement and disagreement across analyses
Confidence Assessment: For each key element, the level of consensus is explicitly evaluated

Implementation Highlights

Multi-Perspective Analysis:

Generates 5 independent analyses for each chunk of frames
Uses 5 distinct prompt templates to encourage diversity:

Standard analytical perspective
Forensic analyst perspective
Detective/law enforcement perspective
Security expert perspective
Witness testimony perspective


Higher temperature settings (0.5) for greater response diversity


Complete Frame Processing:

Processes all frames in chunks of 10 frames each
Each chunk undergoes the full multi-analysis process


Two-Level Consensus Building:

Chunk-Level Consensus: After generating multiple analyses for each chunk, determines consensus on:

Crime type
Perpetrator description
Victim description
Key actions
Evidence
Timeline


Cross-Chunk Consensus: After processing all chunks, synthesizes a final consensus across the entire video

In [13]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from concurrent.futures import ThreadPoolExecutor
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/SELF-CONSISTENCY"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class SelfConsistencyGeminiAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use the same working model as the other scripts
        self.model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.max_frames_per_request = 20
        self.chunk_size = 10
        self.num_independent_runs = 5  # Number of independent analyses for consistency checking
        os.makedirs(self.save_dir, exist_ok=True)

    def make_gemini_request(self, contents, temperature=0.3):
        """Make a single request to Gemini API with specified temperature"""
        url_with_key = f"{self.base_url}?key={self.api_key}"

        payload = {
            "contents": contents,
            "generationConfig": {
                "temperature": temperature,  # Variable temperature for diversity
                "maxOutputTokens": 4096,
                "topP": 0.8,
                "topK": 10
            }
        }

        try:
            response = requests.post(url_with_key, headers=self.headers, json=payload)

            if response.status_code != 200:
                error_detail = response.json() if response.text else response.text
                print(f"API Error {response.status_code}: {error_detail}")
                return f"Error {response.status_code}: {error_detail}"

            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    return result["candidates"][0]["content"]["parts"][0]["text"]
                else:
                    return "Error: No content in response"
            else:
                return "Error: No candidates in response"

        except Exception as e:
            print(f"API request error: {str(e)}")
            return f"Error: {str(e)}"

    def generate_independent_analysis(self, frame_data, run_number, video_id, crime_type):
        """Generate a single independent analysis of the frames"""
        print(f"  Generating independent analysis #{run_number}...")

        # Comprehensive analysis prompt (same for all runs to ensure consistency testing)
        comprehensive_prompt = """Analyze these video frames thoroughly and provide a comprehensive assessment. Please address the following aspects:

1. SCENE DESCRIPTION: Describe the environment, setting, and overall context.

2. PEOPLE IDENTIFICATION: Identify all individuals present, their apparent ages, genders, and relationships.

3. ACTIONS AND BEHAVIORS: Detail what each person is doing and their specific behaviors.

4. INTERACTIONS: Analyze how the people are interacting with each other.

5. BODY LANGUAGE: Examine postures, facial expressions, and non-verbal communication.

6. POWER DYNAMICS: Assess any signs of dominance, submission, control, or vulnerability.

7. CONCERNING ELEMENTS: Identify any red flags, inappropriate behaviors, or signs of potential harm.

8. OVERALL ASSESSMENT: Provide your comprehensive conclusion about what is happening and level of concern.

Be thorough, specific, and evidence-based in your analysis."""

        run_responses = []

        # Use slightly different temperature for each run to encourage diversity
        temperatures = [0.1, 0.2, 0.3, 0.4, 0.5]
        temperature = temperatures[run_number % len(temperatures)]

        # Process frames in chunks for this independent run
        for i in range(0, len(frame_data), self.chunk_size):
            chunk = frame_data[i:i + self.chunk_size]

            # Prepare content parts for Gemini
            parts = [{"text": comprehensive_prompt}]

            # Add images to parts
            for frame in chunk:
                parts.append({
                    "inline_data": {
                        "mime_type": "image/png",
                        "data": frame
                    }
                })

            contents = [{
                "role": "user",
                "parts": parts
            }]

            # Make API request for this chunk
            response = self.make_gemini_request(contents, temperature)
            run_responses.append(response)

            # Rate limiting
            time.sleep(2)

        # Combine responses for this run
        if len(run_responses) == 1:
            combined_response = run_responses[0]
        else:
            combined_response = "\n\n=== NEXT CHUNK ===\n\n".join(run_responses)

        # Save intermediate result for this independent run
        timestamp = time.strftime("%Y%m%d_%H%M%S")
        run_result = {
            f"independent_run_{run_number}": {
                "run_number": run_number,
                "temperature": temperature,
                "analysis": combined_response
            }
        }
        self.save_results(run_result, f"{crime_type}_{video_id}_consistency_run{run_number}_{timestamp}.json")

        return combined_response

    def analyze_consistency(self, independent_analyses):
        """Analyze consistency across independent runs"""
        print("Analyzing consistency across independent analyses...")

        # Create consistency analysis prompt
        consistency_prompt = f"""You have {len(independent_analyses)} independent analyses of the same video frames. Please analyze the consistency across these analyses and provide:

1. CONSISTENT FINDINGS: What observations appear consistently across most or all analyses?

2. INCONSISTENT FINDINGS: What observations vary significantly between analyses?

3. CONFIDENCE LEVELS: Which findings have high confidence (consistent) vs low confidence (inconsistent)?

4. DISCREPANCY ANALYSIS: Where analyses disagree, what might explain the differences?

5. CONSENSUS ASSESSMENT: Based on the most consistent findings, what is the most reliable assessment?

6. RELIABILITY SCORE: Rate the overall reliability of the consensus (1-10 scale).

Here are the independent analyses:

"""

        # Add each independent analysis
        for i, analysis in enumerate(independent_analyses, 1):
            consistency_prompt += f"\n=== INDEPENDENT ANALYSIS #{i} ===\n{analysis}\n"

        consistency_prompt += "\n\nNow provide your consistency analysis:"

        # Make request for consistency analysis
        contents = [{
            "role": "user",
            "parts": [{"text": consistency_prompt}]
        }]

        consistency_analysis = self.make_gemini_request(contents, temperature=0.1)
        return consistency_analysis

    def process_frames_self_consistency(self, frame_data, video_id, crime_type):
        """Process frames using self-consistency prompting strategy"""
        print(f"Starting self-consistency analysis with {self.num_independent_runs} independent runs...")

        # Generate multiple independent analyses
        independent_analyses = []
        for run_num in range(1, self.num_independent_runs + 1):
            print(f"\n--- Independent Run {run_num}/{self.num_independent_runs} ---")
            analysis = self.generate_independent_analysis(frame_data, run_num, video_id, crime_type)
            independent_analyses.append(analysis)
            print(f"  Completed run {run_num}")

            # Longer delay between independent runs
            if run_num < self.num_independent_runs:
                print(f"  Waiting 5 seconds before next independent run...")
                time.sleep(5)

        # Analyze consistency across runs
        print(f"\n--- Consistency Analysis ---")
        consistency_analysis = self.analyze_consistency(independent_analyses)

        # Save consistency analysis separately
        timestamp = time.strftime("%Y%m%d_%H%M%S")
        consistency_result = {
            "consistency_analysis": consistency_analysis
        }
        self.save_results(consistency_result, f"{crime_type}_{video_id}_consistency_analysis_{timestamp}.json")

        # Compile results
        results = {
            "independent_analyses": {},
            "consistency_analysis": consistency_analysis,
            "methodology": {
                "num_runs": self.num_independent_runs,
                "approach": "Multiple independent analyses with consistency checking",
                "temperatures_used": [0.1, 0.2, 0.3, 0.4, 0.5]
            }
        }

        # Store each independent analysis
        for i, analysis in enumerate(independent_analyses, 1):
            results["independent_analyses"][f"run_{i}"] = {
                "run_number": i,
                "analysis": analysis,
                "temperature": [0.1, 0.2, 0.3, 0.4, 0.5][(i-1) % 5]
            }

        return results

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with self-consistency prompting approach"""
        try:
            frame_names = list(frames_data.keys())

            # Improved sorting function for frame numbers
            def extract_frame_number(filename):
                try:
                    # Handle different naming patterns
                    if '_frame_' in filename:
                        parts = filename.split('_frame_')
                        if len(parts) > 1:
                            number_part = parts[1].split('.')[0]
                            return int(number_part)
                    elif 'frame' in filename.lower():
                        # Alternative pattern matching
                        import re
                        numbers = re.findall(r'\d+', filename)
                        if numbers:
                            return int(numbers[-1])  # Use the last number found
                except Exception as e:
                    print(f"Error extracting frame number from {filename}: {str(e)}")
                    return 0

            sorted_frames = sorted(frame_names, key=extract_frame_number)

            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Frame names sample: {sorted_frames[:5]}{'...' if len(sorted_frames) > 5 else ''}")
            print(f"Using model: {self.model_name}")

            results = {}
            timestamp = time.strftime("%Y%m%d_%H%M%S")

            try:
                frame_data = [frames_data[frame_name] for frame_name in sorted_frames
                             if frame_name in frames_data and frames_data[frame_name]]

                if not frame_data:
                    results["Self_Consistency_Analysis"] = {
                        "error": "No valid frames were available for analysis.",
                        "frames_used": len(sorted_frames),
                        "valid_frames": 0,
                        "model_used": self.model_name,
                        "crime_type": crime_type,
                        "prompting_technique": "SELF_CONSISTENCY_PROMPTING"
                    }
                    print("WARNING: No valid frames were available for analysis.")
                else:
                    print(f"Processing {len(frame_data)} valid frames with self-consistency prompting...")
                    consistency_results = self.process_frames_self_consistency(frame_data, video_id, crime_type)

                    results["Self_Consistency_Analysis"] = {
                        "method": "self_consistency_prompting",
                        "description": "Multiple independent analyses with consistency verification",
                        "consistency_results": consistency_results,
                        "frames_used": len(sorted_frames),
                        "valid_frames": len(frame_data),
                        "analysis_timestamp": timestamp,
                        "model_used": self.model_name,
                        "crime_type": crime_type,
                        "prompting_technique": "SELF_CONSISTENCY_PROMPTING"
                    }

                # Save results
                self.save_results(results, f"{crime_type}_{video_id}_self_consistency_analysis_{timestamp}.json")
                print(f"Self-consistency analysis for {video_id} ({crime_type}) completed and saved.")

            except Exception as e:
                print(f"Error processing self-consistency analysis: {str(e)}")
                results["Self_Consistency_Analysis"] = {
                    "method": "self_consistency_prompting",
                    "error": str(e),
                    "frames_used": len(sorted_frames) if 'sorted_frames' in locals() else 0,
                    "model_used": self.model_name,
                    "crime_type": crime_type,
                    "prompting_technique": "SELF_CONSISTENCY_PROMPTING"
                }

            return results

        except Exception as e:
            print(f"Error in analyze_frames: {str(e)}")
            raise

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with self-consistency analysis - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = SelfConsistencyGeminiAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH SELF-CONSISTENCY PROMPTING 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 Self-Consistency Mode: Multiple independent analyses with consistency verification!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with self-consistency prompting approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key} with self-consistency prompting")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"self_consistency_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete self-consistency analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection"""
    print("Testing Gemini API connection...")

    # FIXED: Use the same working model
    model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
    url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

    headers = {
        "Content-Type": "application/json"
    }

    payload = {
        "contents": [
            {
                "parts": [
                    {
                        "text": "Hello, can you respond with 'Gemini API connection successful'?"
                    }
                ]
            }
        ]
    }

    try:
        response = requests.post(url, headers=headers, json=payload)

        if response.status_code == 200:
            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                    print("✓ Gemini API connection successful!")
                    print(f"Response: {response_text}")
                    return True
            print("✗ Unexpected response format")
            print(f"Response: {result}")
            return False
        else:
            print(f"✗ API Error {response.status_code}: {response.text}")
            return False

    except Exception as e:
        print(f"✗ Connection error: {str(e)}")
        return False

def check_authentication():
    """Placeholder function to check authentication"""
    return True

def run():
    """Main execution function"""
    print("Self-Consistency Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*75)
    print("🎯 SELF-CONSISTENCY TECHNIQUE: Multiple independent analyses with consistency verification!")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*75)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection
    if not test_gemini_api(api_key):
        print("✗ Gemini API test failed. Please check your API key and connection.")
        return

    # Check authentication
    if not check_authentication():
        print("✗ Authentication not completed.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING WITH SELF-CONSISTENCY PROMPTING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)
    total_independent_runs = 0

    for video_id, video_results in results.items():
        if video_results and 'Self_Consistency_Analysis' in video_results:
            analysis = video_results['Self_Consistency_Analysis']
            total_frames_processed += analysis.get('valid_frames', 0)
            if 'consistency_results' in analysis and 'methodology' in analysis['consistency_results']:
                total_independent_runs += analysis['consistency_results']['methodology'].get('num_runs', 0)

    print("\n" + "="*75)
    print(f"🎉 COMPLETE SELF-CONSISTENCY PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Total independent runs: {total_independent_runs}")
    print(f"Model used: {analyzer.model_name if 'analyzer' in locals() else 'gemini-2.0-flash'}")
    print(f"Analysis pattern: Multiple Independent → Consistency Check → Consensus")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("🎯 Self-consistency prompting technique applied to all videos")
    print("="*75)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
Self-Consistency Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🎯 SELF-CONSISTENCY TECHNIQUE: Multiple independent analyses with consistency verification!
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/SELF-CONSISTENCY
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...
✓ Gemini API connection successful!
Response: Gemini API connection successful


Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTING COMPLETE FOLDER PROCESSING WITH SELF-CONSISTENCY PROMPTING...

=== DISCOVERING ALL VI

#Meta-Prompting
- Meta-Prompting that processes all frames from crime videos. This technique is unique because it uses the AI to generate its own specialized prompts for analysis.

Meta-Prompting Approach
The Meta-Prompting technique follows this innovative process:

- Prompt Generation: Instead of using predefined prompts, the system asks the AI to create specialized prompts for analyzing video frames
- Prompt Application: These AI-generated prompts are then used to analyze the actual frames
- Meta-Synthesis: The system also generates a specialized synthesis prompt to combine all chunk analyses

Implementation Highlights

Two-Stage Meta-Prompting:

- First Stage: For each chunk of frames, generate a specialized analysis prompt
- Second Stage: For final synthesis, generate a specialized synthesis prompt
- Both stages use the AI to create task-specific prompts rather than using predefined ones


Complete Frame Processing:

- Processes all frames in chunks of 10 frames each
- Each chunk undergoes the full meta-prompting process independently


Specialized Prompt Design Process: Guides the AI to create prompts that focus on:

Step-by-step observation:
- Objective description before interpretation
- Attention to easily missed details
- Organizing observations into a coherent narrative
- Avoids including example responses in the generated prompts


Fallback Safety:

- If meta-prompting fails, falls back to a simple seed prompt
Ensures analysis can continue even if prompt generation has issues

In [14]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from concurrent.futures import ThreadPoolExecutor
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/META-PROMPTING"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class MetaPromptingGeminiAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use the same working model as the other scripts
        self.model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.max_frames_per_request = 20
        self.chunk_size = 10
        os.makedirs(self.save_dir, exist_ok=True)

    def make_gemini_request(self, contents, temperature=0.1):
        """Make a single request to Gemini API"""
        url_with_key = f"{self.base_url}?key={self.api_key}"

        payload = {
            "contents": contents,
            "generationConfig": {
                "temperature": temperature,
                "maxOutputTokens": 4096,
                "topP": 0.8,
                "topK": 10
            }
        }

        try:
            response = requests.post(url_with_key, headers=self.headers, json=payload)

            if response.status_code != 200:
                error_detail = response.json() if response.text else response.text
                print(f"API Error {response.status_code}: {error_detail}")
                return f"Error {response.status_code}: {error_detail}"

            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    return result["candidates"][0]["content"]["parts"][0]["text"]
                else:
                    return "Error: No content in response"
            else:
                return "Error: No candidates in response"

        except Exception as e:
            print(f"API request error: {str(e)}")
            return f"Error: {str(e)}"

    def generate_meta_prompts(self, video_id, crime_type):
        """Meta-prompting phase: Generate optimized prompts for analysis"""
        print("=== META-PROMPTING PHASE: Generating Optimized Analysis Prompts ===")

        meta_prompt = """You are an expert in prompt engineering and crime video analysis. Your task is to design the most effective prompts for analyzing potentially concerning video content.

Given that you will be analyzing video frames that may contain inappropriate or harmful behavior, design specialized prompts for different aspects of the analysis that would maximize accuracy, thoroughness, and reliability.

Create optimized prompts for these 6 key analysis areas:

1. SCENE_ANALYSIS: For understanding the environment and context
2. PERSON_IDENTIFICATION: For identifying individuals and their characteristics
3. BEHAVIOR_ANALYSIS: For analyzing actions and behaviors
4. INTERACTION_DYNAMICS: For understanding relationships and interactions
5. RISK_ASSESSMENT: For identifying concerning elements and red flags
6. COMPREHENSIVE_SYNTHESIS: For creating final assessments

For each area, provide:
- An optimized prompt that would elicit the most accurate and thorough analysis
- Key questions that should be addressed
- Important considerations and potential pitfalls to avoid
- Specific instructions for evidence-based reasoning

Format your response clearly with headers for each analysis area. Make the prompts sophisticated, specific, and designed to maximize analytical quality."""

        contents = [{
            "role": "user",
            "parts": [{"text": meta_prompt}]
        }]

        print("Generating specialized analysis prompts...")
        meta_response = self.make_gemini_request(contents, temperature=0.3)

        # Save meta-prompting phase results
        timestamp = time.strftime("%Y%m%d_%H%M%S")
        meta_result = {
            "meta_prompt_generation": meta_response
        }
        self.save_results(meta_result, f"{crime_type}_{video_id}_meta_generation_{timestamp}.json")

        return meta_response

    def extract_generated_prompts(self, meta_response, video_id, crime_type):
        """Extract and structure the generated prompts"""
        print("Extracting and structuring generated prompts...")

        extraction_prompt = f"""From the following meta-prompting response, extract the specific prompts for each analysis area and format them as a structured JSON object.

Meta-prompting response:
{meta_response}

Extract and format as JSON with this structure:
{{
    "scene_analysis": {{
        "prompt": "extracted prompt text",
        "key_questions": ["question1", "question2", ...],
        "considerations": ["consideration1", "consideration2", ...]
    }},
    "person_identification": {{
        "prompt": "extracted prompt text",
        "key_questions": ["question1", "question2", ...],
        "considerations": ["consideration1", "consideration2", ...]
    }},
    "behavior_analysis": {{
        "prompt": "extracted prompt text",
        "key_questions": ["question1", "question2", ...],
        "considerations": ["consideration1", "consideration2", ...]
    }},
    "interaction_dynamics": {{
        "prompt": "extracted prompt text",
        "key_questions": ["question1", "question2", ...],
        "considerations": ["consideration1", "consideration2", ...]
    }},
    "risk_assessment": {{
        "prompt": "extracted prompt text",
        "key_questions": ["question1", "question2", ...],
        "considerations": ["consideration1", "consideration2", ...]
    }},
    "comprehensive_synthesis": {{
        "prompt": "extracted prompt text",
        "key_questions": ["question1", "question2", ...],
        "considerations": ["consideration1", "consideration2", ...]
    }}
}}

Provide only the JSON structure with the extracted content."""

        contents = [{
            "role": "user",
            "parts": [{"text": extraction_prompt}]
        }]

        extraction_response = self.make_gemini_request(contents, temperature=0.1)

        try:
            # Attempt to parse as JSON, with fallback handling
            import json
            if extraction_response.strip().startswith('{'):
                generated_prompts = json.loads(extraction_response)
            else:
                # If not proper JSON, create a structured fallback
                generated_prompts = self.create_fallback_prompts(meta_response)
        except:
            generated_prompts = self.create_fallback_prompts(meta_response)

        # Save prompt extraction results
        timestamp = time.strftime("%Y%m%d_%H%M%S")
        extraction_result = {
            "prompt_extraction": generated_prompts
        }
        self.save_results(extraction_result, f"{crime_type}_{video_id}_prompt_extraction_{timestamp}.json")

        return generated_prompts

    def create_fallback_prompts(self, meta_response):
        """Create fallback prompts if extraction fails"""
        return {
            "scene_analysis": {
                "prompt": "Analyze the scene environment, setting, location, and overall context visible in these video frames. Consider lighting, objects, spatial layout, and any environmental factors that might be relevant.",
                "key_questions": ["Where is this taking place?", "What type of environment is this?", "What objects and features are visible?"],
                "considerations": ["Note environmental factors that might affect behavior", "Consider privacy vs public settings"]
            },
            "person_identification": {
                "prompt": "Identify all individuals present in the frames. Describe their apparent ages, genders, physical characteristics, clothing, and positioning. Consider their relationships and roles.",
                "key_questions": ["How many people are present?", "What are their apparent ages and characteristics?", "What relationships do they appear to have?"],
                "considerations": ["Be objective about descriptions", "Note power imbalances based on age/size"]
            },
            "behavior_analysis": {
                "prompt": "Analyze the specific behaviors, actions, and movements of each person. Focus on what they are doing, how they are moving, and their physical interactions.",
                "key_questions": ["What specific actions is each person performing?", "How are they moving or positioned?", "What physical interactions are occurring?"],
                "considerations": ["Distinguish between voluntary and involuntary behaviors", "Note any signs of distress or discomfort"]
            },
            "interaction_dynamics": {
                "prompt": "Examine the interpersonal dynamics and relationships between individuals. Analyze communication patterns, body language, and social dynamics.",
                "key_questions": ["How are people interacting with each other?", "What does body language suggest?", "Who appears to be leading interactions?"],
                "considerations": ["Look for signs of consent vs coercion", "Note power dynamics and control patterns"]
            },
            "risk_assessment": {
                "prompt": "Identify any concerning elements, red flags, or indicators of inappropriate or harmful behavior. Focus on signs that warrant concern or further attention.",
                "key_questions": ["What concerning elements are present?", "Are there signs of inappropriate behavior?", "What risks or harms might be indicated?"],
                "considerations": ["Be specific about concerning observations", "Consider context and alternative explanations"]
            },
            "comprehensive_synthesis": {
                "prompt": "Synthesize all previous analyses into a comprehensive assessment. Integrate findings from scene, people, behaviors, interactions, and risks into a coherent conclusion.",
                "key_questions": ["What is the overall picture?", "How do all observations fit together?", "What is the level of concern?"],
                "considerations": ["Base conclusions on evidence", "Acknowledge limitations and uncertainties"]
            }
        }

    def apply_generated_prompts(self, frame_data, generated_prompts, video_id, crime_type):
        """Apply the meta-generated prompts to analyze the frames"""
        print("=== APPLICATION PHASE: Using Generated Prompts for Analysis ===")

        analysis_results = {}

        # Define the analysis sequence
        analysis_sequence = [
            "scene_analysis",
            "person_identification",
            "behavior_analysis",
            "interaction_dynamics",
            "risk_assessment",
            "comprehensive_synthesis"
        ]

        # Apply each generated prompt
        for analysis_type in analysis_sequence:
            if analysis_type in generated_prompts:
                print(f"\nApplying {analysis_type.replace('_', ' ').title()} prompt...")

                prompt_data = generated_prompts[analysis_type]
                optimized_prompt = prompt_data.get("prompt", "")
                key_questions = prompt_data.get("key_questions", [])
                considerations = prompt_data.get("considerations", [])

                # Enhance prompt with key questions and considerations
                full_prompt = f"{optimized_prompt}\n\nKey questions to address:\n"
                for q in key_questions:
                    full_prompt += f"- {q}\n"

                full_prompt += f"\nImportant considerations:\n"
                for c in considerations:
                    full_prompt += f"- {c}\n"

                full_prompt += f"\nProvide a thorough analysis addressing these points."

                # Apply to frame chunks
                type_responses = []
                for i in range(0, len(frame_data), self.chunk_size):
                    chunk = frame_data[i:i + self.chunk_size]

                    # Prepare content parts for Gemini
                    parts = [{"text": full_prompt}]

                    # Add images to parts
                    for frame in chunk:
                        parts.append({
                            "inline_data": {
                                "mime_type": "image/png",
                                "data": frame
                            }
                        })

                    contents = [{
                        "role": "user",
                        "parts": parts
                    }]

                    response = self.make_gemini_request(contents)
                    type_responses.append(response)

                    time.sleep(3)

                # Combine responses for this analysis type
                if len(type_responses) == 1:
                    combined_response = type_responses[0]
                else:
                    combined_response = "\n\n=== NEXT CHUNK ===\n\n".join(type_responses)

                analysis_results[analysis_type] = {
                    "generated_prompt": optimized_prompt,
                    "key_questions": key_questions,
                    "considerations": considerations,
                    "analysis_result": combined_response
                }

                # Save individual analysis type results
                timestamp = time.strftime("%Y%m%d_%H%M%S")
                type_result = {
                    analysis_type: analysis_results[analysis_type]
                }
                self.save_results(type_result, f"{crime_type}_{video_id}_meta_{analysis_type}_{timestamp}.json")

                print(f"Completed {analysis_type.replace('_', ' ')} analysis")

        return analysis_results

    def evaluate_prompt_effectiveness(self, analysis_results, video_id, crime_type):
        """Evaluate the effectiveness of the generated prompts"""
        print("=== EVALUATION PHASE: Assessing Prompt Effectiveness ===")

        evaluation_prompt = f"""Evaluate the effectiveness of the meta-generated prompts based on the analysis results below.

For each analysis type, assess:
1. PROMPT QUALITY: How well did the generated prompt elicit thorough analysis?
2. COMPLETENESS: Did the analysis address all intended aspects?
3. SPECIFICITY: How specific and detailed were the results?
4. RELEVANCE: How relevant were the findings to crime video analysis?
5. ACTIONABILITY: How useful are the insights for decision-making?

Rate each aspect 1-10 and provide improvement suggestions.

Analysis Results:
{json.dumps(analysis_results, indent=2)}

Provide your evaluation in a structured format."""

        contents = [{
            "role": "user",
            "parts": [{"text": evaluation_prompt}]
        }]

        evaluation_response = self.make_gemini_request(contents)

        # Save evaluation results
        timestamp = time.strftime("%Y%m%d_%H%M%S")
        evaluation_result = {
            "effectiveness_evaluation": evaluation_response
        }
        self.save_results(evaluation_result, f"{crime_type}_{video_id}_meta_evaluation_{timestamp}.json")

        return evaluation_response

    def process_frames_meta_prompting(self, frame_data, video_id, crime_type):
        """Process frames using meta-prompting strategy"""
        print("Starting meta-prompting analysis...")

        # Phase 1: Generate optimized prompts
        meta_response = self.generate_meta_prompts(video_id, crime_type)

        # Phase 2: Extract and structure prompts
        generated_prompts = self.extract_generated_prompts(meta_response, video_id, crime_type)

        # Phase 3: Apply generated prompts
        analysis_results = self.apply_generated_prompts(frame_data, generated_prompts, video_id, crime_type)

        # Phase 4: Evaluate prompt effectiveness
        evaluation = self.evaluate_prompt_effectiveness(analysis_results, video_id, crime_type)

        # Compile complete meta-prompting results
        meta_prompting_results = {
            "meta_prompting_process": {
                "phase_1_meta_generation": meta_response,
                "phase_2_prompt_extraction": generated_prompts,
                "phase_3_analysis_application": analysis_results,
                "phase_4_effectiveness_evaluation": evaluation
            },
            "methodology": {
                "approach": "Meta-prompting with self-generated optimized prompts",
                "phases": [
                    "Meta-prompt generation",
                    "Prompt extraction and structuring",
                    "Application of generated prompts",
                    "Effectiveness evaluation"
                ]
            }
        }

        return meta_prompting_results

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with meta-prompting approach"""
        try:
            frame_names = list(frames_data.keys())

            # Improved sorting function for frame numbers
            def extract_frame_number(filename):
                try:
                    # Handle different naming patterns
                    if '_frame_' in filename:
                        parts = filename.split('_frame_')
                        if len(parts) > 1:
                            number_part = parts[1].split('.')[0]
                            return int(number_part)
                    elif 'frame' in filename.lower():
                        # Alternative pattern matching
                        import re
                        numbers = re.findall(r'\d+', filename)
                        if numbers:
                            return int(numbers[-1])  # Use the last number found
                except Exception as e:
                    print(f"Error extracting frame number from {filename}: {str(e)}")
                    return 0

            sorted_frames = sorted(frame_names, key=extract_frame_number)

            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Frame names sample: {sorted_frames[:5]}{'...' if len(sorted_frames) > 5 else ''}")
            print(f"Using model: {self.model_name}")

            results = {}
            timestamp = time.strftime("%Y%m%d_%H%M%S")

            try:
                frame_data = [frames_data[frame_name] for frame_name in sorted_frames
                             if frame_name in frames_data and frames_data[frame_name]]

                if not frame_data:
                    results["Meta_Prompting_Analysis"] = {
                        "error": "No valid frames were available for analysis.",
                        "frames_used": len(sorted_frames),
                        "valid_frames": 0,
                        "model_used": self.model_name,
                        "crime_type": crime_type,
                        "prompting_technique": "META_PROMPTING"
                    }
                    print("WARNING: No valid frames were available for analysis.")
                else:
                    print(f"Processing {len(frame_data)} valid frames with meta-prompting...")
                    meta_results = self.process_frames_meta_prompting(frame_data, video_id, crime_type)

                    results["Meta_Prompting_Analysis"] = {
                        "method": "meta_prompting",
                        "description": "Self-generated optimized prompts for enhanced analysis",
                        "meta_prompting_results": meta_results,
                        "frames_used": len(sorted_frames),
                        "valid_frames": len(frame_data),
                        "analysis_timestamp": timestamp,
                        "model_used": self.model_name,
                        "crime_type": crime_type,
                        "prompting_technique": "META_PROMPTING"
                    }

                # Save results
                self.save_results(results, f"{crime_type}_{video_id}_meta_prompting_analysis_{timestamp}.json")
                print(f"Meta-prompting analysis for {video_id} ({crime_type}) completed and saved.")

            except Exception as e:
                print(f"Error processing meta-prompting analysis: {str(e)}")
                results["Meta_Prompting_Analysis"] = {
                    "method": "meta_prompting",
                    "error": str(e),
                    "frames_used": len(sorted_frames) if 'sorted_frames' in locals() else 0,
                    "model_used": self.model_name,
                    "crime_type": crime_type,
                    "prompting_technique": "META_PROMPTING"
                }

            return results

        except Exception as e:
            print(f"Error in analyze_frames: {str(e)}")
            raise

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with meta-prompting analysis - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = MetaPromptingGeminiAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH META-PROMPTING 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 Meta-Prompting Mode: Self-generated optimized prompts for enhanced analysis!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with meta-prompting approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key} with meta-prompting")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"meta_prompting_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete meta-prompting analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection"""
    print("Testing Gemini API connection...")

    # FIXED: Use the same working model
    model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
    url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

    headers = {
        "Content-Type": "application/json"
    }

    payload = {
        "contents": [
            {
                "parts": [
                    {
                        "text": "Hello, can you respond with 'Gemini API connection successful'?"
                    }
                ]
            }
        ]
    }

    try:
        response = requests.post(url, headers=headers, json=payload)

        if response.status_code == 200:
            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                    print("✓ Gemini API connection successful!")
                    print(f"Response: {response_text}")
                    return True
            print("✗ Unexpected response format")
            print(f"Response: {result}")
            return False
        else:
            print(f"✗ API Error {response.status_code}: {response.text}")
            return False

    except Exception as e:
        print(f"✗ Connection error: {str(e)}")
        return False

def check_authentication():
    """Placeholder function to check authentication"""
    return True

def run():
    """Main execution function"""
    print("Meta-Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*75)
    print("🎯 META-PROMPTING TECHNIQUE: Self-generated optimized prompts for enhanced analysis!")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*75)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection
    if not test_gemini_api(api_key):
        print("✗ Gemini API test failed. Please check your API key and connection.")
        return

    # Check authentication
    if not check_authentication():
        print("✗ Authentication not completed.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING WITH META-PROMPTING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)
    total_phases_completed = 0

    for video_id, video_results in results.items():
        if video_results and 'Meta_Prompting_Analysis' in video_results:
            analysis = video_results['Meta_Prompting_Analysis']
            total_frames_processed += analysis.get('valid_frames', 0)
            if 'meta_prompting_results' in analysis and 'methodology' in analysis['meta_prompting_results']:
                total_phases_completed += len(analysis['meta_prompting_results']['methodology'].get('phases', []))

    print("\n" + "="*75)
    print(f"🎉 COMPLETE META-PROMPTING PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Total meta-phases completed: {total_phases_completed}")
    print(f"Model used: {analyzer.model_name if 'analyzer' in locals() else 'gemini-2.0-flash'}")
    print(f"Analysis pattern: Generate → Extract → Apply → Evaluate")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("🎯 Meta-prompting technique applied to all videos")
    print("="*75)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
Meta-Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🎯 META-PROMPTING TECHNIQUE: Self-generated optimized prompts for enhanced analysis!
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/META-PROMPTING
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...
✓ Gemini API connection successful!
Response: Gemini API connection successful


Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTING COMPLETE FOLDER PROCESSING WITH META-PROMPTING...

=== DISCOVERING ALL VIDEOS AND FRAMES ===
Scanning dire

#Chain-Of-Thought Prompting
Chain of Thought (CoT) prompting approach that processes all frames from crime videos. This technique explicitly encourages the model to show its

step-by-step reasoning process.
- Chain of Thought Prompting Approach: The Chain of Thought technique follows this explicit reasoning process:

Step-by-Step Reasoning: The approach explicitly asks the model to "think step by step" through its analysis
- Transparent Reasoning: Each reasoning step is clearly articulated in the response
- Structured Progression: The analysis follows a logical progression from observation to conclusion
- Reasoning Synthesis: The final synthesis also uses step-by-step reasoning to connect all segments

Implementation Highlights

Structured Reasoning Steps:

The prompt breaks down the analysis into 6 clear steps:

- Objective observation without interpretation
- Identification of key actors
- Chronological sequence of events
- Important objects and their usage
- Context and setting analysis
- Integration of observations into a coherent description


Each step builds on the previous one in a logical progression


Complete Frame Processing:

- Processes all frames in chunks of 10 frames each
- Each chunk undergoes the full chain of thought process independently


Reasoning-Based Synthesis: The synthesis prompt also follows a chain of thought structure:

- Extraction of key information from each segment
- Timeline construction across all segments
- Tracking people across multiple segments
- Tracking objects across segments
- Contextual integration of segments
- Construction of a comprehensive description


This ensures the synthesis uses the same reasoning approach as individual chunks


Explicit Prompting for Reasoning:

- Both the analysis and synthesis prompts specifically ask to "think step by step"
- System messages reinforce the importance of step-by-step reasoning
The model is explicitly asked to show its thinking process at each step

In [15]:
import os
import json
import base64
import requests
import time
from datetime import datetime
from collections import defaultdict

# Add Google Drive mounting for Colab
try:
    from google.colab import drive
    drive.mount('/content/drive')
    print("Google Drive mounted successfully!")
except ImportError:
    print("Not running in Colab or drive module not available")

# Configuration
DATA_DIR = "/home/opade7/Documents/gpu-test/crime-data"
SAVE_DIR = "/home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/CHAIN-OF-THOUGHT"
FRAME_INTERVAL = 1  # Process ALL frames (set to higher number for sampling)

class ChainOfThoughtGeminiAnalyzer:
    def __init__(self, api_key):
        self.api_key = api_key
        # FIXED: Use the same working model as the other scripts
        self.model_name = "gemini-2.0-flash"  # Changed from "gemini-2.5-pro"
        self.base_url = f"https://generativelanguage.googleapis.com/v1beta/models/{self.model_name}:generateContent"
        self.headers = {
            "Content-Type": "application/json"
        }
        self.save_dir = SAVE_DIR
        self.chunk_size = 10
        os.makedirs(self.save_dir, exist_ok=True)

        # Chain of Thought prompt template
        self.cot_prompt_template = """
Analyze these video frames using a chain of thought reasoning process. Think step by step as you examine what's happening:

Step 1: First, carefully observe and list what you can actually see in the frames. Note people, objects, settings, and actions without interpretation.

Step 2: Identify the key actors in the scene. Describe each person's appearance and what they are doing. Track individuals across multiple frames.

Step 3: Describe the sequence of events chronologically. What happens first, next, and after that?

Step 4: Note any important objects or items in the scene and how they're being used.

Step 5: Consider the context and setting. Where is this taking place? What kind of environment is shown?

Step 6: Based on all the above observations, describe what appears to be happening in these frames.

Make sure to clearly show your thinking process for each step. These are frames {frame_range} of {total_frames}.
"""

        # Chain of Thought synthesis prompt
        self.cot_synthesis_prompt = """
You are going to synthesize multiple analyses of different segments of the same video into a coherent understanding of the entire sequence. Use chain of thought reasoning to connect all segments into a complete narrative.

Think through the following steps:

Step 1: Review each segment analysis and extract the key information about people, objects, and actions from each one.

Step 2: Create a timeline by arranging events across all segments in chronological order.

Step 3: Identify which people appear across multiple segments and track their actions throughout.

Step 4: Note how objects or items are used or moved across the entire sequence.

Step 5: Consider the overall context and how different segments relate to each other.

Step 6: Based on all the above reasoning, construct a comprehensive description of what happens throughout the entire video.

Show your thinking at each step as you build your understanding of the complete video sequence.
"""

    def make_gemini_request(self, contents, temperature=0.1):
        """Make a single request to Gemini API"""
        url_with_key = f"{self.base_url}?key={self.api_key}"

        payload = {
            "contents": contents,
            "generationConfig": {
                "temperature": temperature,
                "maxOutputTokens": 4096,
                "topP": 0.8,
                "topK": 10
            }
        }

        try:
            response = requests.post(url_with_key, headers=self.headers, json=payload)

            if response.status_code != 200:
                error_detail = response.json() if response.text else response.text
                print(f"API Error {response.status_code}: {error_detail}")
                return f"Error {response.status_code}: {error_detail}"

            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    return result["candidates"][0]["content"]["parts"][0]["text"]
                else:
                    return "Error: No content in response"
            else:
                return "Error: No candidates in response"

        except Exception as e:
            print(f"API request error: {str(e)}")
            return f"Error: {str(e)}"

    def _format_chunk_analyses(self, all_chunk_analyses):
        """Helper method to format chunk analyses for synthesis"""
        formatted_chunks = []
        for analysis in all_chunk_analyses:
            chunk_text = f"SEGMENT {analysis['chunk']} (Frames {analysis['frame_range']}):\n{analysis['analysis']}\n\n{'-' * 40}\n"
            formatted_chunks.append(chunk_text)

        return ''.join(formatted_chunks)

    def process_frames_with_cot(self, frames_data, video_id, crime_type):
        """Process frames with chain of thought prompting approach"""
        # Extract frame data from the dictionary
        frame_names = list(frames_data.keys())

        # Improved sorting function for frame numbers
        def extract_frame_number(filename):
            try:
                # Handle different naming patterns
                if '_frame_' in filename:
                    parts = filename.split('_frame_')
                    if len(parts) > 1:
                        number_part = parts[1].split('.')[0]
                        return int(number_part)
                elif 'frame' in filename.lower():
                    # Alternative pattern matching
                    import re
                    numbers = re.findall(r'\d+', filename)
                    if numbers:
                        return int(numbers[-1])  # Use the last number found
            except Exception as e:
                print(f"Error extracting frame number from {filename}: {str(e)}")
                return 0

        sorted_frames = sorted(frame_names, key=extract_frame_number)
        frame_data = [frames_data[frame_name] for frame_name in sorted_frames if frame_name in frames_data and frames_data[frame_name]]

        if not frame_data:
            return {"error": "No valid frames available for analysis"}

        total_frames = len(frame_data)
        print(f"Processing all {total_frames} frames with chain of thought approach")

        # Process all frames by dividing them into chunks
        chunk_size = 10
        frame_chunks = [frame_data[i:i+chunk_size] for i in range(0, total_frames, chunk_size)]
        print(f"Split into {len(frame_chunks)} chunks of approximately {chunk_size} frames each")

        # Initialize results
        cot_results = {}
        all_chunk_analyses = []

        # Process each chunk of frames
        for chunk_idx, chunk in enumerate(frame_chunks):
            frame_start = chunk_idx * chunk_size + 1
            frame_end = min((chunk_idx + 1) * chunk_size, total_frames)
            frame_range = f"{frame_start}-{frame_end}"

            print(f"Processing chunk {chunk_idx+1}/{len(frame_chunks)} (frames {frame_range})...")

            # Initialize chunk results
            chunk_results = {
                "frame_range": frame_range
            }

            # Format the CoT prompt for this chunk
            formatted_cot_prompt = self.cot_prompt_template.format(frame_range=frame_range, total_frames=total_frames)

            # Prepare content parts for Gemini
            parts = [{"text": formatted_cot_prompt}]

            # Add frames to parts
            for frame in chunk:
                parts.append({
                    "inline_data": {
                        "mime_type": "image/png",
                        "data": frame
                    }
                })

            # Create contents for Gemini
            contents = [{
                "role": "user",
                "parts": parts
            }]

            try:
                print(f"  Sending request to Gemini for chunk {chunk_idx+1}...")
                cot_analysis = self.make_gemini_request(contents, temperature=0.1)

                if not cot_analysis.startswith("Error"):
                    print(f"  Received response for chunk {chunk_idx+1}")

                    # Save the CoT analysis
                    chunk_results["cot_analysis"] = cot_analysis

                    # Add to collection of all chunk analyses
                    all_chunk_analyses.append({
                        "chunk": chunk_idx + 1,
                        "frame_range": frame_range,
                        "analysis": cot_analysis
                    })
                else:
                    print(f"  Error in CoT analysis for chunk {chunk_idx+1}: {cot_analysis}")
                    chunk_results["error"] = cot_analysis

            except Exception as e:
                print(f"  Error in CoT analysis for chunk {chunk_idx+1}: {str(e)}")
                chunk_results["error"] = str(e)

            # Save results for this chunk
            cot_results[f"Chunk {chunk_idx+1}"] = chunk_results

            # Save intermediate results for this chunk
            timestamp = time.strftime("%Y%m%d_%H%M%S")
            chunk_result = {
                f"Chunk {chunk_idx+1}": chunk_results
            }
            self.save_results(chunk_result, f"{crime_type}_{video_id}_cot_chunk{chunk_idx+1}_{timestamp}.json")
            print(f"  Results for chunk {chunk_idx+1} saved")

            # Rate limiting between chunks
            print(f"  Waiting 3 seconds before next chunk...")
            time.sleep(3)

        # After processing all chunks, generate a synthesis using CoT
        if all_chunk_analyses:
            print("Generating chain of thought synthesis across all chunks...")

            # Create synthesis prompt with all chunk analyses
            synthesis_text = f"""
{self.cot_synthesis_prompt}

Here are the analyses for each segment of the video:

{'-' * 40}
{self._format_chunk_analyses(all_chunk_analyses)}

Think step by step to synthesize these segments into a complete understanding of the video.
"""

            # Create contents for synthesis
            synthesis_contents = [{
                "role": "user",
                "parts": [{"text": synthesis_text}]
            }]

            try:
                print("Sending request for final synthesis...")
                cot_synthesis = self.make_gemini_request(synthesis_contents, temperature=0.1)

                if not cot_synthesis.startswith("Error"):
                    print("Synthesis complete!")

                    # Save CoT synthesis
                    cot_results["Chain of Thought Synthesis"] = {
                        "synthesis": cot_synthesis
                    }

                    # Save synthesis separately
                    timestamp = time.strftime("%Y%m%d_%H%M%S")
                    synthesis_result = {
                        "Chain of Thought Synthesis": cot_results["Chain of Thought Synthesis"]
                    }
                    self.save_results(synthesis_result, f"{crime_type}_{video_id}_cot_synthesis_{timestamp}.json")
                    print("Synthesis results saved")
                else:
                    print(f"Error in CoT synthesis: {cot_synthesis}")
                    cot_results["Chain of Thought Synthesis"] = {
                        "error": cot_synthesis
                    }
            except Exception as e:
                print(f"Error in CoT synthesis: {str(e)}")
                cot_results["Chain of Thought Synthesis"] = {
                    "error": str(e)
                }

        return {
            "cot_results": cot_results,
            "frames_used": total_frames,
            "chunks_processed": len(frame_chunks),
            "frames_per_chunk": chunk_size,
            "model_used": self.model_name,  # Track which model was used
            "crime_type": crime_type,
            "prompting_technique": "CHAIN_OF_THOUGHT_PROMPTING"
        }

    def save_results(self, results, filename):
        """Save results to a file"""
        filepath = os.path.join(self.save_dir, filename)
        with open(filepath, 'w') as f:
            json.dump(results, f, indent=2)
        print(f"Results saved to: {filepath}")

    def analyze_frames(self, frames_data, video_id, crime_type):
        """Analyze frames with chain of thought prompting"""
        try:
            print(f"\n=== ANALYZING VIDEO: {video_id} ({crime_type}) WITH CHAIN OF THOUGHT PROMPTING ===")
            print(f"Total frames loaded: {len(frames_data)}")
            print(f"Using model: {self.model_name}")

            timestamp = time.strftime("%Y%m%d_%H%M%S")
            results = self.process_frames_with_cot(frames_data, video_id, crime_type)

            # Save complete results
            self.save_results(results, f"{crime_type}_{video_id}_cot_complete_{timestamp}.json")
            print(f"Complete chain of thought analysis for {video_id} ({crime_type}) saved.")

            return results

        except Exception as e:
            print(f"Error in chain of thought analysis: {str(e)}")
            return {"error": str(e)}

def discover_all_videos_and_frames(data_dir):
    """Discover all crime types, videos, and their frames - PROCESSES ENTIRE FOLDER STRUCTURE"""
    print(f"\n=== DISCOVERING ALL VIDEOS AND FRAMES ===")
    print(f"Scanning directory: {data_dir}")

    all_videos = {}

    try:
        # Get all subdirectories (crime types) - THIS PROCESSES ALL CRIME FOLDERS
        crime_types = [d for d in os.listdir(data_dir)
                      if os.path.isdir(os.path.join(data_dir, d))]

        print(f"Found {len(crime_types)} crime type directories: {crime_types}")

        # PROCESS EVERY SINGLE CRIME TYPE FOLDER
        for crime_type in crime_types:
            crime_dir = os.path.join(data_dir, crime_type)
            print(f"\nScanning {crime_type} directory...")

            try:
                all_files = os.listdir(crime_dir)
                print(f"  Found {len(all_files)} files")

                # Group files by video ID - PROCESSES ALL FILES IN EACH FOLDER
                video_groups = defaultdict(list)

                for filename in all_files:
                    # Skip non-image files
                    if not any(filename.lower().endswith(ext) for ext in ['.png', '.jpg', '.jpeg', '.bmp']):
                        continue

                    # Extract video ID from filename
                    video_id = extract_video_id_from_filename(filename)
                    if video_id:
                        video_groups[video_id].append(filename)

                print(f"  Identified {len(video_groups)} unique videos:")
                for video_id, frames in video_groups.items():
                    print(f"    {video_id}: {len(frames)} frames")
                    all_videos[f"{crime_type}_{video_id}"] = {
                        'crime_type': crime_type,
                        'video_id': video_id,
                        'frames': frames,
                        'crime_dir': crime_dir
                    }

            except Exception as e:
                print(f"  Error scanning {crime_type}: {str(e)}")

    except Exception as e:
        print(f"Error accessing main directory: {str(e)}")

    print(f"\nTotal videos discovered: {len(all_videos)}")
    print("✓ ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    return all_videos

def extract_video_id_from_filename(filename):
    """Extract video ID from filename using various patterns"""
    import re

    # Remove file extension
    name_without_ext = os.path.splitext(filename)[0]

    # Pattern 1: VideoName_something_frame_number
    if '_frame_' in name_without_ext:
        parts = name_without_ext.split('_frame_')
        return parts[0]

    # Pattern 2: VideoName_number (assuming last part is frame number)
    parts = name_without_ext.split('_')
    if len(parts) >= 2:
        # Check if last part is a number
        try:
            int(parts[-1])
            return '_'.join(parts[:-1])
        except ValueError:
            pass

    # Pattern 3: Just use the filename without numbers at the end
    video_id = re.sub(r'_?\d+$', '', name_without_ext)
    if video_id and video_id != name_without_ext:
        return video_id

    # Pattern 4: If all else fails, use the whole name (assuming single frame)
    return name_without_ext

def load_frames_for_video(video_info, frame_interval=1):
    """Load every Nth frame for a specific video (default: ALL frames)"""
    frames_data = {}
    crime_dir = video_info['crime_dir']
    frame_files = video_info['frames']
    video_id = video_info['video_id']

    print(f"\nLoading {'ALL frames' if frame_interval == 1 else f'every {frame_interval}th frame'} for {video_id}...")

    # Sort frames by frame number
    def extract_frame_number(filename):
        try:
            import re
            numbers = re.findall(r'\d+', filename)
            if numbers:
                return int(numbers[-1])  # Use the last number found
        except Exception:
            pass
        return 0

    frame_files.sort(key=extract_frame_number)

    # Select every Nth frame
    selected_frames = frame_files[::frame_interval]
    if frame_interval == 1:
        print(f"  Processing ALL {len(selected_frames)} frames")
    else:
        print(f"  Selected {len(selected_frames)} frames from {len(frame_files)} total frames")

    # Load selected frames
    for idx, frame_file in enumerate(selected_frames):
        frame_path = os.path.join(crime_dir, frame_file)
        try:
            with open(frame_path, 'rb') as f:
                frame_data = base64.b64encode(f.read()).decode('utf-8')
                frames_data[frame_file] = frame_data

            # Show progress
            if idx < 3 or idx % 10 == 0 or idx == len(selected_frames) - 1:
                original_idx = frame_files.index(frame_file)
                print(f"  Loaded: {frame_file} (frame #{original_idx + 1}, {os.path.getsize(frame_path)/1024:.1f} KB)")

        except Exception as e:
            print(f"  Error loading frame {frame_file}: {str(e)}")

    if frame_interval == 1:
        print(f"Successfully loaded ALL {len(frames_data)} frames for {video_id}")
    else:
        print(f"Successfully loaded {len(frames_data)} frames for {video_id} (every {frame_interval}th frame)")
    return frames_data

def process_all_crime_folders(api_key):
    """Process ALL crime folders with chain of thought prompting - PROCESSES ENTIRE DIRECTORY STRUCTURE"""
    # Initialize analyzer
    analyzer = ChainOfThoughtGeminiAnalyzer(api_key)

    # Discover ALL videos and frames in the entire folder structure
    all_videos = discover_all_videos_and_frames(DATA_DIR)

    if not all_videos:
        print("No videos found to process!")
        return {}

    all_results = {}
    skipped_videos = []

    print(f"\n🔥 PROCESSING ALL {len(all_videos)} VIDEOS WITH CHAIN OF THOUGHT PROMPTING 🔥")
    print(f"Using model: {analyzer.model_name}")
    print(f"Frame processing: {'ALL frames' if FRAME_INTERVAL == 1 else f'Every {FRAME_INTERVAL}th frame'}")
    print("🎯 Chain of Thought Mode: Step-by-step reasoning with explicit thinking process!")
    print("📁 ENTIRE FOLDER STRUCTURE WILL BE PROCESSED")
    print("="*70)

    # Process EVERY SINGLE VIDEO discovered
    for video_key, video_info in all_videos.items():
        print(f"\nProcessing video: {video_key}")
        print(f"  Crime type: {video_info['crime_type']}")
        print(f"  Video ID: {video_info['video_id']}")
        print(f"  Frames available: {len(video_info['frames'])}")

        try:
            # Load frames for this video (every Nth frame as configured)
            frames_data = load_frames_for_video(video_info, frame_interval=FRAME_INTERVAL)

            if frames_data:
                # Analyze frames with chain of thought prompting approach
                results = analyzer.analyze_frames(
                    frames_data,
                    video_info['video_id'],
                    video_info['crime_type']
                )
                all_results[video_key] = results
                print(f"✓ Successfully processed {video_key} with chain of thought prompting")
            else:
                print(f"✗ No frames loaded for video {video_key} - skipping")
                skipped_videos.append(f"{video_key} (no frames loaded)")

        except Exception as e:
            print(f"✗ Error processing video {video_key}: {str(e)}")
            skipped_videos.append(f"{video_key} (error: {str(e)})")

    # Save summary results
    summary_file = os.path.join(SAVE_DIR, f"cot_summary_{time.strftime('%Y%m%d_%H%M%S')}.json")
    with open(summary_file, 'w') as f:
        json.dump(all_results, f, indent=2)

    # Log skipped videos
    if skipped_videos:
        skipped_file = os.path.join(SAVE_DIR, f"skipped_videos_{time.strftime('%Y%m%d_%H%M%S')}.txt")
        with open(skipped_file, 'w') as f:
            f.write("Videos that could not be processed:\n")
            for video in skipped_videos:
                f.write(f"{video}\n")
        print(f"\nSkipped {len(skipped_videos)} videos. List saved to: {skipped_file}")

    print(f"\nComplete chain of thought analysis saved to: {summary_file}")
    print(f"Successfully processed {len(all_results)} videos out of {len(all_videos)} total")

    return all_results

def test_gemini_api(api_key):
    """Test Gemini API connection"""
    print("Testing Gemini API connection...")

    # FIXED: Use the same working model (was inconsistent with "gemini-2.0-flash-exp")
    model_name = "gemini-2.0-flash"  # Changed from "gemini-2.0-flash-exp"
    url = f"https://generativelanguage.googleapis.com/v1beta/models/{model_name}:generateContent?key={api_key}"

    headers = {
        "Content-Type": "application/json"
    }

    payload = {
        "contents": [
            {
                "parts": [
                    {
                        "text": "Hello, can you respond with 'Gemini API connection successful'?"
                    }
                ]
            }
        ]
    }

    try:
        response = requests.post(url, headers=headers, json=payload)

        if response.status_code == 200:
            result = response.json()
            if "candidates" in result and result["candidates"]:
                if "content" in result["candidates"][0] and "parts" in result["candidates"][0]["content"]:
                    response_text = result["candidates"][0]["content"]["parts"][0]["text"]
                    print("✓ Gemini API connection successful!")
                    print(f"Response: {response_text}")
                    return True
            print("✗ Unexpected response format")
            print(f"Response: {result}")
            return False
        else:
            print(f"✗ API Error {response.status_code}: {response.text}")
            return False

    except Exception as e:
        print(f"✗ Connection error: {str(e)}")
        return False

def run():
    """Main execution function"""
    print("Chain of Thought Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING")
    print("="*75)
    print("🎯 CHAIN OF THOUGHT TECHNIQUE: Step-by-step reasoning with explicit thinking process!")
    print("📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS")
    print("="*75)

    # Test directory access first
    print("Testing directory access...")
    for path in [DATA_DIR, SAVE_DIR]:
        print(f"Path: {path}")
        print(f"  Exists: {os.path.exists(path)}")
        if os.path.exists(path):
            try:
                contents = os.listdir(path)
                print(f"  Contains {len(contents)} items")
                if contents:
                    print(f"  First few items: {contents[:3]}")
            except Exception as e:
                print(f"  Error accessing contents: {str(e)}")

    # Get API key
    try:
        api_key_path = "/home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt"
        print(f"Trying to load API key from: {api_key_path}")
        print(f"File exists: {os.path.exists(api_key_path)}")

        f = open(api_key_path, "r")
        api_key = f.read().strip()
        f.close()

        if not api_key:
            print("✗ Failed to load Gemini API key: File is empty")
            return

        print("✓ Successfully loaded Gemini API key")
        print(f"API key starts with: {api_key[:10]}...")

    except Exception as e:
        print(f"✗ Failed to load Gemini API key: {str(e)}")
        return

    # Test Gemini API connection
    if not test_gemini_api(api_key):
        print("✗ Gemini API test failed. Please check your API key and connection.")
        return

    # Verify directories exist
    print("\nVerifying directories:")
    print(f"Data directory exists: {os.path.exists(DATA_DIR)}")
    print(f"Save directory exists: {os.path.exists(SAVE_DIR)}")

    if not os.path.exists(DATA_DIR):
        print(f"✗ Data directory not found: {DATA_DIR}")
        return

    # Create save directory if it doesn't exist
    os.makedirs(SAVE_DIR, exist_ok=True)

    # Process ALL crime folders - ENTIRE DIRECTORY STRUCTURE
    print("\n🚀 STARTING COMPLETE FOLDER PROCESSING WITH CHAIN OF THOUGHT PROMPTING...")
    results = process_all_crime_folders(api_key)

    # Print summary
    total_frames_processed = 0
    total_videos_processed = len(results)
    total_chunks_processed = 0

    for video_id, video_results in results.items():
        if video_results and 'cot_results' in video_results:
            total_frames_processed += video_results.get('frames_used', 0)
            total_chunks_processed += video_results.get('chunks_processed', 0)

    print("\n" + "="*75)
    print(f"🎉 COMPLETE CHAIN OF THOUGHT PROCESSING FINISHED!")
    print(f"Videos processed: {total_videos_processed}")
    print(f"Total frames analyzed: {total_frames_processed}")
    print(f"Total chunks processed: {total_chunks_processed}")
    print(f"Model used: {analyzer.model_name if 'analyzer' in locals() else 'gemini-2.0-flash'}")
    print(f"Analysis pattern: Step 1 → Step 2 → ... → Step 6 → Synthesis")
    print("📁 ENTIRE FOLDER STRUCTURE WAS PROCESSED")
    print("🎯 Chain of thought prompting technique applied to all videos")
    print("="*75)

if __name__ == "__main__":
    run()

Not running in Colab or drive module not available
Chain of Thought Prompting Crime Video Analysis with Gemini - ENTIRE FOLDER PROCESSING
🎯 CHAIN OF THOUGHT TECHNIQUE: Step-by-step reasoning with explicit thinking process!
📁 PROCESSES ALL VIDEOS IN ALL CRIME TYPE FOLDERS
Testing directory access...
Path: /home/opade7/Documents/gpu-test/crime-data
  Exists: True
  Contains 11 items
  First few items: ['Burglary', 'Stealing', 'Fighting']
Path: /home/opade7/Documents/gpu-test/RESULT-PROMPT/GEMINI/CHAIN-OF-THOUGHT
  Exists: False
Trying to load API key from: /home/opade7/Documents/gpu-test/API-KEYS/Gemini.txt
File exists: True
✓ Successfully loaded Gemini API key
API key starts with: AIzaSyBGql...
Testing Gemini API connection...
✓ Gemini API connection successful!
Response: Gemini API connection successful


Verifying directories:
Data directory exists: True
Save directory exists: False

🚀 STARTING COMPLETE FOLDER PROCESSING WITH CHAIN OF THOUGHT PROMPTING...

=== DISCOVERING ALL VIDEOS A